In [1]:
#!/usr/bin/python
# -*- coding: utf-8 -*-
# ========== python ==========
import os
from pathlib import Path
from logging import Logger
from typing import List, Dict, Tuple, Optional, Union, Callable, Final, Literal, get_args
from operator import itemgetter, attrgetter
import itertools
from IPython.display import display

from utils.setup import setup_logger, get_device
from const.const_values import PROJECT_DIR

os.chdir(PROJECT_DIR)
logger: Logger = setup_logger(__name__, f'{PROJECT_DIR}/log/jupyter_run.log')
device = get_device(device_name='cpu', logger=logger)

In [2]:
# jupyter
import seaborn as sns
import matplotlib.pyplot as plt
# Machine learning
import numpy as np
import pandas as pd
import h5py
import optuna
# torch
import torch
from torch.nn import CrossEntropyLoss
from torch.utils.data import Dataset
from torch.utils.data.dataloader import DataLoader
from torch.utils.tensorboard.writer import SummaryWriter
# torch ignite
from ignite.engine import Engine
from ignite.handlers import Checkpoint
# My items
from models.datasets.data_helper import MyDataHelper, MyDataLoaderHelper, DefaultTokens
from models.datasets.datasets_for_story import StoryTriple
# My utils
from utils.setup import load_param
from utils.torch import load_model, torch_fix_seed
# main function
from run_for_KGC import main_function

In [3]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 100)

In [4]:
from const.const_values import CPU, MODEL
from models.KGModel.kg_model import HEAD, RELATION, TAIL
from utils.torch_ignite import TRAINER, EVALUATOR
from const.const_values import DATASETS, DATA_HELPER, DATA_LOADERS, TRAIN_RETURNS

In [5]:
SEED: Final[int] = 42
args_path = f'{PROJECT_DIR}/models/230201/01/param.pkl'
model_path = f'{PROJECT_DIR}/models/230201/01/model.pth'

In [6]:
args = load_param(args_path)

# args.pre_train = True
args.logger = logger
args.device = device
args.batch_size = 1
args.pre_train=False
args.init_embedding_using_bert = False
args.model_path = model_path
args.only_load_trainer_evaluator = True
args.old_data = 1

del args.optuna_file, args.device_name, args.pid, args.study_name, args.n_trials

In [7]:
args

Namespace(notebook=False, console_level='info', logfile='models/230201/01/log.log', param_file='models/230201/01/param.pkl', train_anyway=True, tensorboard_dir='models/230201/01/tensorboard', checkpoint_dir='models/230201/01/checkpoint/', model_path='/Users/ryoyakaneda/Documents/学校/M1Study/knowledge_graph/models/230201/01/model.pth', resume_from_checkpoint=False, resume_from_last_point=False, only_load_trainer_evaluator=True, resume_checkpoint_path=None, pre_train=False, train_valid_test=True, only_train=False, use_for_challenge100=False, use_for_challenge090=False, use_for_challenge075=False, use_title=None, do_optuna=False, story_special_num=5, relation_special_num=5, entity_special_num=5, padding_token_e=0, cls_token_e=1, mask_token_e=2, sep_token_e=3, bos_token_e=4, padding_token_r=0, cls_token_r=1, mask_token_r=2, sep_token_r=3, bos_token_r=4, padding_token_s=0, cls_token_s=1, mask_token_s=2, sep_token_s=3, bos_token_s=4, model_version='03', embedding_dim=128, entity_embedding_dim

In [8]:
"embedding_dim={}, entity_embedding_dim={}, relation_embedding_dim={}, nhead={}, num_layers={}, ".format(
    args.embedding_dim, args.entity_embedding_dim, args.relation_embedding_dim, args.nhead, args.num_layers,)

'embedding_dim=128, entity_embedding_dim=768, relation_embedding_dim=64, nhead=4, num_layers=4, '

In [9]:
torch_fix_seed(seed=SEED)
return_dict = main_function(args, logger=logger)

2023-02-05 09:46:00 - INFO - run_for_KGC.py - 901 - ----- make datahelper start. -----
2023-02-05 09:46:00 - INFO - run_for_KGC.py - 591 - ----- use old data (version 1) -----
2023-02-05 09:46:00 - INFO - data_helper.py - 333 - ====== Show MyRawData ======
2023-02-05 09:46:00 - INFO - data_helper.py - 334 - entity num: 7844
2023-02-05 09:46:00 - INFO - data_helper.py - 335 - relation num: 63
2023-02-05 09:46:00 - INFO - data_helper.py - 336 - ====== Show MyRawData ======
2023-02-05 09:46:00 - INFO - data_helper.py - 607 - ========== Show DataHelper ==========
2023-02-05 09:46:00 - INFO - data_helper.py - 333 - ====== Show MyRawData ======
2023-02-05 09:46:00 - INFO - data_helper.py - 334 - entity num: 7844
2023-02-05 09:46:00 - INFO - data_helper.py - 335 - relation num: 63
2023-02-05 09:46:00 - INFO - data_helper.py - 336 - ====== Show MyRawData ======
2023-02-05 09:46:00 - INFO - data_helper.py - 609 - entity_special_dicts: {0: '<pad_e>', 1: '<cls_e>', 2: '<mask_e>', 3: '<sep_e>', 4:

In [10]:
model = return_dict[MODEL]

dataset_train: StoryTriple = return_dict[DATASETS][0]
triple: torch.Tensor = dataset_train.triple
data_helper: MyDataHelper = return_dict[DATA_HELPER]
evaluator: Checkpoint = return_dict[TRAIN_RETURNS][EVALUATOR]

load_model(model, args.model_path, device)
model.eval()

entities, relations = data_helper.processed_entities, data_helper.processed_relations
d_e, d_r = {e: i for i, e in enumerate(entities)}, {r: i for i, r in enumerate(relations)}

triple_df = pd.DataFrame([(entities[_t[0]], relations[_t[1]], entities[_t[2]]) for _t in triple], columns=[HEAD, RELATION, TAIL])
story_entities = triple_df[HEAD].tolist()

### One of the inputs is shown as an example.

### The sequence contains triples from the beginning of each scene to the specified length. In this case, the length is set to 512.

In [11]:
print("training sequence shape:", dataset_train[0].shape)
dataset_train[0]

training sequence shape: torch.Size([512, 3])


tensor([[   4,    4,    4],
        [3960,   46,   24],
        [3960,   26,   24],
        ...,
        [4069,   33,  219],
        [   4,    4,    4],
        [4070,   38,  208]])

#### Note that the data presented in the previous section are part of this series below.

In [12]:
triple_df[triple_df['head'].str.contains('ResidentPatient')]

head          relation                           tail
9349    ResidentPatient:001       kgc:subject                AllTitle:Holmes
9350    ResidentPatient:001  kgc:hasPredicate           word.predicate:guess
9351    ResidentPatient:001          kgc:what            ResidentPatient:002
9352    ResidentPatient:001          kgc:what            ResidentPatient:004
9353    ResidentPatient:001          kgc:when  ResidentPatient:1889-10-20T22
...                     ...               ...                            ...
10794   ResidentPatient:324   kgc:hasProperty            word.predicate:want
10795   ResidentPatient:324          kgc:what           ResidentPatient:324a
10797  ResidentPatient:324a       kgc:subject    ResidentPatient:Blessington
10798  ResidentPatient:324a   kgc:hasProperty            word.predicate:hide
10799  ResidentPatient:324a          kgc:what   ResidentPatient:Own_identity

[1110 rows x 3 columns]

This is the model made by Pytorch.

In [13]:
model

KgStoryTransformer03(
  (entity_embeddings): Embedding(7849, 768, padding_idx=0)
  (relation_embeddings): Embedding(68, 64, padding_idx=0)
  (pe): PositionalEncoding(
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (transformer): TransformerEncoder(
    (layers): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=128, out_features=128, bias=True)
        )
        (linear1): Linear(in_features=128, out_features=1028, bias=True)
        (dropout): Dropout(p=0.1, inplace=False)
        (linear2): Linear(in_features=1028, out_features=128, bias=True)
        (norm1): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (norm2): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (dropout1): Dropout(p=0.1, inplace=False)
        (dropout2): Dropout(p=0.1, inplace=False)
        (activation): GELU(approximate='none')
      )
      (1): TransformerEncoderLayer(
      

This function is used to visualize Attention. The description is skipped.

In [14]:
# This is sub functions for getting Attention.
def extract(_model, target, inputs):
    """This is sub functions for getting Attention.

    """
    features = None

    def forward_hook(_module, _inputs, _):
        nonlocal features
        x, _, _ = _inputs
        outputs = _module.forward(x, x, x, need_weights=True)[1]
        features = outputs.detach().clone()

    handle = target.register_forward_hook(forward_hook)

    _model.eval()
    _model(inputs, torch.LongTensor([[]]), torch.LongTensor([[]]), torch.LongTensor([[]]))

    handle.remove()

    return features

# This is main functions for getting Attention.
def get_attention(input_):
    """This is main functions for getting Attention.

    """
    assert len(input_) == 1
    features = extract(model, model.transformer.layers[-1].self_attn, input_)[0]
    df_attention = pd.DataFrame([[entities[h], relations[r], entities[t]]+[features[j, i].item() for j in range(len(features))] for i, (h, r, t) in enumerate(input_[0])])
    df_attention.columns=[HEAD, RELATION, TAIL] + [f'atten_from{i}' for i in range(len(df_attention.columns)-3)]
    return df_attention

def show_attention_heatmap(df_attention):
    sns.heatmap(df_attention.iloc[:,3:])
    plt.show()

In [15]:
MASK_E = DefaultTokens.MASK_E
KILL = 'word.predicate:kill'

TAKE = 'word.predicate:take'
BRING = 'word.predicate:bring'
DIE = 'word.predicate:die'
HIDE = 'word.predicate:hide'

The input to the model is the following function's "question_".
There are some last scenes and criminal scene after last scene.
Each part of criminal scene are changed into a victim or <mask>, and the MASK part is estimated.

In [16]:
bos_triple = [d_e[DefaultTokens.BOS_E], d_r[DefaultTokens.BOS_R],d_e[DefaultTokens.BOS_E]]
mask_e_id = d_e[DefaultTokens.MASK_E]
Holmes_id =d_e['AllTitle:Holmes']

def make_ranking(from_story_name, to_story_name, predicate_, whom_, subject_, why_, what_, where_):
    if not (from_story_name is None and to_story_name is None):
        _start_index = story_entities.index(from_story_name)-1
        _end_index = len(story_entities) - story_entities[::-1].index(to_story_name)
    else:
        _start_index = 0
        _end_index = 0
    question_ = torch.tensor(
        [
            # [... last 80 scenes ...],
            # ...
            bos_triple,
            [mask_e_id, d_r['kgc:infoSource'],     Holmes_id      ],
            [mask_e_id, d_r['kgc:hasPredicate'],   d_e[predicate_]],
            [mask_e_id, d_r['kgc:whom'],           d_e[whom_     ]],
            [mask_e_id, d_r['kgc:subject'],        d_e[subject_  ]],
            [mask_e_id, d_r['kgc:why'],            d_e[why_      ]],
            [mask_e_id, d_r['kgc:what'],           d_e[what_     ]],
            [mask_e_id, d_r['kgc:where'],          d_e[where_    ]],
        ]
    )
    mask_ = torch.zeros_like(question_, dtype=torch.bool) # not mask all position
    mask_[1:, 0] = True                                   # where head position without bos token
    mask_[1:, 2] = True                                   # where tail position without bos token

    last_triples = triple[_start_index: _end_index]

    questions = torch.cat([last_triples, question_], dim=0).unsqueeze(0)
    masks = torch.cat([torch.zeros_like(last_triples), mask_], dim=0).to(torch.bool).transpose(1,0).unsqueeze(0)

    data_list = []
    with torch.no_grad():
        _, (story_pred, relation_pred, entity_pred) = model(questions, masks[:,0], masks[:,1], masks[:,2])
        sorted_ = torch.argsort(entity_pred, dim=1, descending=True)
        for i in range(sorted_.shape[1]):
            ans_= sorted_[:, i]
            info_source_, predicate_pred, whom_pred, subject_pred, why_pred, what_pred, where_pred = ans_
            data_list.append([entities[predicate_pred], entities[whom_pred], entities[subject_pred], entities[why_pred], entities[what_pred], entities[where_pred]])
    df_ranking = pd.DataFrame(data_list, columns=['predicate', 'whom', 'subject', 'why', 'what', 'where'])
    df_attension = get_attention(questions)

    return df_ranking, df_attension

In [17]:
def main_func01(_title, _victim_name, criminal, predicate, _last_index, _story_len):
    from_ = f'{_title}:{_last_index-_story_len+1}'
    to_ = f'{_title}:{_last_index}'
    predicate = predicate
    victim = f'{_title}:{_victim_name}'
    criminal = f'{_title}:{criminal}'
    df_ranking, df_attension = make_ranking(
        from_, to_, predicate, victim, MASK_E, MASK_E, MASK_E, MASK_E)
    df_ranking.index.name='ranking'

    pred_rank = df_ranking.index[df_ranking['subject']==criminal].tolist()
    pred_rank = pred_rank[0] if len(pred_rank)==1 else -1
    logger.info(f"The pred ranking about {criminal} is {pred_rank}")
    display(df_ranking.iloc[:max(20, pred_rank)])
    len_ = len(df_attension)
    for i in range(len_-10, len_):
        print(f"index={i}, triple={df_attension.iloc[i,:3].tolist()}, attention list")
        display(df_attension.sort_values(f'atten_from{i}', ascending=False).iloc[:,[0,1,2,3+i]],)
    return df_ranking, df_attension

def check_killer(_title, _victim_name, _killer_name, _last_index, _story_len):
    return main_func01(_title, _victim_name, _killer_name, KILL, _last_index, _story_len)

# Estimate Criminals

### SpeckledBand(まだらの紐)
Who killed Julia? (criminal & explanation)
被害者: Julia
犯人: Roylott
犯行に用いたもの: snake
犯行動機: 母の相続財産を独占したい

### Input sequence is like this.


|     head     | relation  |            tail            |
|:------------:|:---------:|:--------------------------:|
| SpeckledBand |  stories  |            ...             |
|     ...      |    ...    |            ...             |
|    \<bos>    |  \<bos>   |           \<bos>           |
|  \<unknown>  | predicate |            kill            |
|  \<unknown>  |   whom    |           Julia            |
|  \<unknown>  |  subject  | \<mask(Answer is Roylott)> |
|  \<unknown>  |    why    |          \<mask>           |
|  \<unknown>  |   what    |          \<mask>           |
|  \<unknown>  |    why    |          \<mask>           |

In [18]:
def do_SpeckledBand_pred():
    title = 'SpeckledBand'
    victim_name = 'Julia'
    killer_name = 'Roylott'
    last_index = 401
    story_len = 80

    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention
do_SpeckledBand_pred()
pass

2023-02-05 09:46:01 - INFO - 3696358453.py - 13 - The pred ranking about SpeckledBand:Roylott is 1


predicate                            whom  \
ranking                                                                      
0                      word.predicate:kill              SpeckledBand:Julia   
1                          AllTitle:Holmes            SpeckledBand:Roylott   
2                       word.predicate:die              SpeckledBand:snake   
3                    DancingMen:Abe_Slaney               DevilsFoot:George   
4                    SpeckledBand:dog_whip             word.predicate:meet   
5                     word.predicate:enter         word.predicate:notExist   
6                       SilverBlaze:police    DateTime:1881-04-01T00:00:00   
7              ResidentPatient:Elderly_man             word.predicate:send   
8                      word.predicate:have          word.predicate:receive   
9                SpeckledBand:rope_of_bell   AbbeyGrange:Lady_Brackenstall   
10                      SpeckledBand:Julia                SpeckledBand:bed   
11                      SpeckledBand:snake        SilverBlaze:Edith_Baxter   
12                    word.predicate:exist              word.predicate:sit   
13       DevilsFoot:cottage_of_Pordeux_Bay    DateTime:1883-04-01T15:00:00   
14                  ACaseOfIdentity:Hosmer          word.predicate:confirm   
15                  word.predicate:notHave               DancingMen:Cubitt   
16           AbbeyGrange:Thought_of_Holmes  SpeckledBand:Roylott_s_bedroom   
17                  word.predicate:support                 AllTitle:Holmes   
18                     word.predicate:come                 AllTitle:Watson   
19                      SpeckledBand:Helen             word.predicate:lose   

                                subject                             why  \
ranking                                                                   
0                    SpeckledBand:snake                 AllTitle:Watson   
1                  SpeckledBand:Roylott        SilverBlaze:Edith_Baxter   
2                               <bos_e>  SpeckledBand:Roylott_s_bedroom   
3                    SpeckledBand:Julia              SpeckledBand:Julia   
4                     DevilsFoot:George   AbbeyGrange:Lady_Brackenstall   
5                   word.predicate:meet    DateTime:1883-04-02T04:00:00   
6              AbbeyGrange:cord_of_bell    DateTime:1883-04-01T23:00:00   
7               word.predicate:notExist            AbbeyGrange:Criminal   
8                    word.predicate:sit            word.predicate:exist   
9                       AllTitle:Watson      ResidentPatient:Helper_boy   
10                    DancingMen:Cubitt             word.predicate:have   
11           SpeckledBand:1883-04-01T10     ResidentPatient:Elderly_man   
12                      AllTitle:Holmes                 AllTitle:Holmes   
13               word.predicate:receive       SpeckledBand:rope_of_bell   
14                 word.predicate:think             word.predicate:mean   
15                  word.predicate:send             word.predicate:send   
16               ACaseOfIdentity:Hosmer         word.predicate:notExist   
17               word.predicate:notHave             word.predicate:meet   
18       SpeckledBand:Roylott_s_bedroom          word.predicate:equalTo   
19                   word.predicate:die      SpeckledBand:1881-04-01T03   

                                   what                            where  
ranking                                                                   
0                               <bos_e>                          <bos_e>  
1                       AllTitle:Holmes          word.predicate:notExist  
2                       AllTitle:Watson   SpeckledBand:Roylott_s_bedroom  
3               word.predicate:notExist                  AllTitle:Holmes  
4                  SpeckledBand:Roylott             SpeckledBand:Roylott  
5                   word.predicate:meet  SpeckledBand:mansion_of_Roylott  
6                SilverBlaze:Ned_Hunter                  AllTitle

index=380, triple=['SpeckledBand:401', 'kgc:subject', 'SpeckledBand:Roma'], attention list


head          relation  \
380  SpeckledBand:401       kgc:subject   
337  SpeckledBand:392       kgc:subject   
134  SpeckledBand:349       kgc:subject   
175  SpeckledBand:358       kgc:subject   
149  SpeckledBand:352       kgc:subject   
359  SpeckledBand:397       kgc:subject   
324  SpeckledBand:389       kgc:subject   
123  SpeckledBand:347       kgc:subject   
381  SpeckledBand:401   kgc:hasProperty   
83   SpeckledBand:338       kgc:subject   
360  SpeckledBand:397   kgc:hasProperty   
320  SpeckledBand:388       kgc:subject   
69   SpeckledBand:335       kgc:subject   
284  SpeckledBand:379       kgc:subject   
145  SpeckledBand:351       kgc:subject   
162  SpeckledBand:355       kgc:subject   
208  SpeckledBand:365       kgc:subject   
362  SpeckledBand:397          kgc:time   
139  SpeckledBand:350       kgc:subject   
375  SpeckledBand:400       kgc:subject   
328  SpeckledBand:390       kgc:subject   
383          <mask_e>    kgc:infoSource   
202  SpeckledBand:364       kgc:subject   
292  SpeckledBand:381       kgc:subject   
354  SpeckledBand:396       kgc:subject   
378  SpeckledBand:400          kgc:time   
257  SpeckledBand:374       kgc:subject   
80   SpeckledBand:337       kgc:subject   
361  SpeckledBand:397          kgc:when   
118  SpeckledBand:346       kgc:subject   
357  SpeckledBand:396          kgc:time   
385          <mask_e>          kgc:whom   
364  SpeckledBand:398       kgc:subject   
368  SpeckledBand:398          kgc:time   
106  SpeckledBand:343         kgc:where   
373  SpeckledBand:399          kgc:time   
228  SpeckledBand:368         kgc:where   
230  SpeckledBand:368          kgc:time   
6    SpeckledBand:323       kgc:subject   
171  SpeckledBand:357       kgc:subject   
74   SpeckledBand:336       kgc:subject   
329  SpeckledBand:390       kgc:subject   
190  SpeckledBand:361          kgc:what   
298  SpeckledBand:383       kgc:subject   
229  SpeckledBand:368          kgc:when   
226  SpeckledBand:368       kgc:subject   
367  SpeckledBand:398          kgc:when   
70   SpeckledBand:335   kgc:hasProperty   
315  SpeckledBand:387       kgc:subject   
340  SpeckledBand:393       kgc:subject   
199  SpeckledBand:363       kgc:subject   
387          <mask_e>           kgc:why   
258  SpeckledBand:374   kgc:hasProperty   
65   SpeckledBand:334   kgc:hasProperty   
119  SpeckledBand:346   kgc:hasProperty   
370  SpeckledBand:399       kgc:subject   
352  SpeckledBand:395          kgc:time   
151  SpeckledBand:352         kgc:where   
262  SpeckledBand:375       kgc:subject   
200  SpeckledBand:363   kgc:hasProperty   
37   SpeckledBand:329       kgc:subject   
43   SpeckledBand:330       kgc:subject   
389          <mask_e>         kgc:where   
172  SpeckledBand:357   kgc:hasProperty   
150  SpeckledBand:352          kgc:what   
146  SpeckledBand:351   kgc:hasProperty   
351  SpeckledBand:395          kgc:when   
71   SpeckledBand:335   kgc:hasProperty   
142  SpeckledBand:350          kgc:when   
347  SpeckledBand:394          kgc:what   
180  SpeckledBand:359       kgc:subject   
286  SpeckledBand:379         kgc:where   
34   SpeckledBand:328       kgc:subject   
135  SpeckledBand:349   kgc:hasProperty   
377  SpeckledBand:400          kgc:what   
356  SpeckledBand:396          kgc:when   
18   SpeckledBand:325          kgc:whom   
312  SpeckledBand:386       kgc:subject   
345  SpeckledBand:394       kgc:subject   
260  SpeckledBand:374          kgc:when   
120  SpeckledBand:346          kgc:when   
64   SpeckledBand:334       kgc:subject   
254  SpeckledBand:373          kgc:when   
243  SpeckledBand:371       kgc:subject   
46   SpeckledBand:330          kgc:time   
204  SpeckledBand:364    kgc:infoSource   
86   SpeckledBand:338          kgc:when   
173  SpeckledBand:357          kgc:when   
205  SpeckledBand:364          kgc:when   
4    SpeckledBand:322          kgc:time   
51   SpeckledBand:331          kgc:time   
252  SpeckledBand:372          kgc:when   
72   SpeckledBand:

index=381, triple=['SpeckledBand:401', 'kgc:hasProperty', 'word.predicate:band'], attention list


...

head          relation  \
76   SpeckledBand:336  kgc:hasPredicate   
360  SpeckledBand:397   kgc:hasProperty   
158  SpeckledBand:354  kgc:hasPredicate   
290  SpeckledBand:380   kgc:hasProperty   
70   SpeckledBand:335   kgc:hasProperty   
357  SpeckledBand:396          kgc:time   
84   SpeckledBand:338  kgc:hasPredicate   
362  SpeckledBand:397          kgc:time   
355  SpeckledBand:396  kgc:hasPredicate   
86   SpeckledBand:338          kgc:when   
368  SpeckledBand:398          kgc:time   
205  SpeckledBand:364          kgc:when   
71   SpeckledBand:335   kgc:hasProperty   
376  SpeckledBand:400  kgc:hasPredicate   
14   SpeckledBand:324          kgc:time   
32   SpeckledBand:327          kgc:time   
352  SpeckledBand:395          kgc:time   
81   SpeckledBand:337          kgc:when   
196  SpeckledBand:362          kgc:when   
175  SpeckledBand:358       kgc:subject   
230  SpeckledBand:368          kgc:time   
373  SpeckledBand:399          kgc:time   
378  SpeckledBand:400          kgc:time   
337  SpeckledBand:392       kgc:subject   
51   SpeckledBand:331          kgc:time   
72   SpeckledBand:335   kgc:hasProperty   
381  SpeckledBand:401   kgc:hasProperty   
380  SpeckledBand:401       kgc:subject   
384          <mask_e>  kgc:hasPredicate   
217  SpeckledBand:366          kgc:when   
55   SpeckledBand:332          kgc:time   
4    SpeckledBand:322          kgc:time   
385          <mask_e>          kgc:whom   
143  SpeckledBand:350          kgc:time   
200  SpeckledBand:363   kgc:hasProperty   
232  SpeckledBand:369       kgc:subject   
10   SpeckledBand:323          kgc:time   
162  SpeckledBand:355       kgc:subject   
255  SpeckledBand:373          kgc:time   
258  SpeckledBand:374   kgc:hasProperty   
26   SpeckledBand:326          kgc:time   
208  SpeckledBand:365       kgc:subject   
206  SpeckledBand:364          kgc:time   
278  SpeckledBand:377          kgc:time   
134  SpeckledBand:349       kgc:subject   
20   SpeckledBand:325          kgc:time   
298  SpeckledBand:383       kgc:subject   
46   SpeckledBand:330          kgc:time   
377  SpeckledBand:400          kgc:what   
7    SpeckledBand:323  kgc:hasPredicate   
119  SpeckledBand:346   kgc:hasProperty   
183  SpeckledBand:359          kgc:time   
267  SpeckledBand:375          kgc:time   
197  SpeckledBand:362          kgc:time   
282  SpeckledBand:378          kgc:time   
61   SpeckledBand:333          kgc:when   
204  SpeckledBand:364    kgc:infoSource   
293  SpeckledBand:381   kgc:hasProperty   
156  SpeckledBand:353          kgc:time   
359  SpeckledBand:397       kgc:subject   
160  SpeckledBand:354          kgc:when   
383          <mask_e>    kgc:infoSource   
77   SpeckledBand:336          kgc:when   
187  SpeckledBand:360          kgc:time   
85   SpeckledBand:338    kgc:infoSource   
191  SpeckledBand:361          kgc:when   
87   SpeckledBand:338          kgc:time   
226  SpeckledBand:368       kgc:subject   
78   SpeckledBand:336          kgc:time   
103  SpeckledBand:341          kgc:time   
142  SpeckledBand:350          kgc:when   
12   SpeckledBand:324  kgc:hasPredicate   
210  SpeckledBand:365    kgc:infoSource   
212  SpeckledBand:365          kgc:time   
65   SpeckledBand:334   kgc:hasProperty   
224  SpeckledBand:367          kgc:time   
247  SpeckledBand:371          kgc:time   
265  SpeckledBand:375    kgc:infoSource   
203  SpeckledBand:364  kgc:hasPredicate   
129  SpeckledBand:348   kgc:hasProperty   
182  SpeckledBand:359          kgc:when   
41   SpeckledBand:329          kgc:time   
146  SpeckledBand:351   kgc:hasProperty   
216  SpeckledBand:366          kgc:what   
135  SpeckledBand:349   kgc:hasProperty   
137  SpeckledBand:349          kgc:time   
67   SpeckledBand:334          kgc:time   
62   SpeckledBand:333          kgc:time   
66   SpeckledBand:334          kgc:when   
273  SpeckledBand:376          kgc:time   
218  SpeckledBand:366          kgc:time   
356  SpeckledBand:396          kgc:when   
166  SpeckledBand:

index=388, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
275  SpeckledBand:377  kgc:hasPredicate   
12   SpeckledBand:324  kgc:hasPredicate   
237  SpeckledBand:370  kgc:hasPredicate   
7    SpeckledBand:323  kgc:hasPredicate   
244  SpeckledBand:371  kgc:hasPredicate   
154  SpeckledBand:353  kgc:hasPredicate   
215  SpeckledBand:366  kgc:hasPredicate   
337  SpeckledBand:392       kgc:subject   
221  SpeckledBand:367  kgc:hasPredicate   
385          <mask_e>          kgc:whom   
299  SpeckledBand:383  kgc:hasPredicate   
376  SpeckledBand:400  kgc:hasPredicate   
371  SpeckledBand:399  kgc:hasPredicate   
365  SpeckledBand:398  kgc:hasPredicate   
232  SpeckledBand:369       kgc:subject   
285  SpeckledBand:379  kgc:hasPredicate   
383          <mask_e>    kgc:infoSource   
281  SpeckledBand:378  kgc:hasPredicate   
175  SpeckledBand:358       kgc:subject   
386          <mask_e>       kgc:subject   
230  SpeckledBand:368          kgc:time   
345  SpeckledBand:394       kgc:subject   
208  SpeckledBand:365       kgc:subject   
1    SpeckledBand:322  kgc:hasPredicate   
298  SpeckledBand:383       kgc:subject   
380  SpeckledBand:401       kgc:subject   
355  SpeckledBand:396  kgc:hasPredicate   
134  SpeckledBand:349       kgc:subject   
309  SpeckledBand:385  kgc:hasPredicate   
210  SpeckledBand:365    kgc:infoSource   
143  SpeckledBand:350          kgc:time   
226  SpeckledBand:368       kgc:subject   
263  SpeckledBand:375  kgc:hasPredicate   
368  SpeckledBand:398          kgc:time   
84   SpeckledBand:338  kgc:hasPredicate   
123  SpeckledBand:347       kgc:subject   
340  SpeckledBand:393       kgc:subject   
324  SpeckledBand:389       kgc:subject   
362  SpeckledBand:397          kgc:time   
357  SpeckledBand:396          kgc:time   
316  SpeckledBand:387  kgc:hasPredicate   
373  SpeckledBand:399          kgc:time   
162  SpeckledBand:355       kgc:subject   
328  SpeckledBand:390       kgc:subject   
312  SpeckledBand:386       kgc:subject   
206  SpeckledBand:364          kgc:time   
228  SpeckledBand:368         kgc:where   
209  SpeckledBand:365  kgc:hasPredicate   
212  SpeckledBand:365          kgc:time   
137  SpeckledBand:349          kgc:time   
378  SpeckledBand:400          kgc:time   
315  SpeckledBand:387       kgc:subject   
124  SpeckledBand:347  kgc:hasPredicate   
127  SpeckledBand:347          kgc:time   
76   SpeckledBand:336  kgc:hasPredicate   
359  SpeckledBand:397       kgc:subject   
352  SpeckledBand:395          kgc:time   
325  SpeckledBand:389  kgc:hasPredicate   
103  SpeckledBand:341          kgc:time   
181  SpeckledBand:359  kgc:hasPredicate   
255  SpeckledBand:373          kgc:time   
156  SpeckledBand:353          kgc:time   
320  SpeckledBand:388       kgc:subject   
335  SpeckledBand:391          kgc:time   
151  SpeckledBand:352         kgc:where   
224  SpeckledBand:367          kgc:time   
145  SpeckledBand:351       kgc:subject   
195  SpeckledBand:362  kgc:hasPredicate   
59   SpeckledBand:333  kgc:hasPredicate   
284  SpeckledBand:379       kgc:subject   
149  SpeckledBand:352       kgc:subject   
278  SpeckledBand:377          kgc:time   
389          <mask_e>         kgc:where   
85   SpeckledBand:338    kgc:infoSource   
30   SpeckledBand:327  kgc:hasPredicate   
158  SpeckledBand:354  kgc:hasPredicate   
100  SpeckledBand:341  kgc:hasPredicate   
87   SpeckledBand:338          kgc:time   
23   SpeckledBand:326  kgc:hasPredicate   
125  SpeckledBand:347         kgc:where   
89   SpeckledBand:339       kgc:subject   
204  SpeckledBand:364    kgc:infoSource   
132  SpeckledBand:348          kgc:time   
139  SpeckledBand:350       kgc:subject   
321  SpeckledBand:388  kgc:hasPredicate   
187  SpeckledBand:360          kgc:time   
354  SpeckledBand:396       kgc:subject   
34   SpeckledBand:328       kgc:subject   
364  SpeckledBand:398       kgc:subject   
372  SpeckledBand:399            kgc:to   
78   SpeckledBand:336          kgc:time   
329  SpeckledBand:390       kgc:subject   
17   SpeckledBand:

index=389, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
337  SpeckledBand:392       kgc:subject   
383          <mask_e>    kgc:infoSource   
175  SpeckledBand:358       kgc:subject   
385          <mask_e>          kgc:whom   
324  SpeckledBand:389       kgc:subject   
298  SpeckledBand:383       kgc:subject   
143  SpeckledBand:350          kgc:time   
230  SpeckledBand:368          kgc:time   
340  SpeckledBand:393       kgc:subject   
368  SpeckledBand:398          kgc:time   
312  SpeckledBand:386       kgc:subject   
373  SpeckledBand:399          kgc:time   
345  SpeckledBand:394       kgc:subject   
315  SpeckledBand:387       kgc:subject   
320  SpeckledBand:388       kgc:subject   
232  SpeckledBand:369       kgc:subject   
328  SpeckledBand:390       kgc:subject   
208  SpeckledBand:365       kgc:subject   
378  SpeckledBand:400          kgc:time   
380  SpeckledBand:401       kgc:subject   
134  SpeckledBand:349       kgc:subject   
362  SpeckledBand:397          kgc:time   
123  SpeckledBand:347       kgc:subject   
237  SpeckledBand:370  kgc:hasPredicate   
137  SpeckledBand:349          kgc:time   
226  SpeckledBand:368       kgc:subject   
162  SpeckledBand:355       kgc:subject   
12   SpeckledBand:324  kgc:hasPredicate   
359  SpeckledBand:397       kgc:subject   
154  SpeckledBand:353  kgc:hasPredicate   
335  SpeckledBand:391          kgc:time   
357  SpeckledBand:396          kgc:time   
124  SpeckledBand:347  kgc:hasPredicate   
372  SpeckledBand:399            kgc:to   
275  SpeckledBand:377  kgc:hasPredicate   
228  SpeckledBand:368         kgc:where   
67   SpeckledBand:334          kgc:time   
387          <mask_e>           kgc:why   
366  SpeckledBand:398            kgc:to   
389          <mask_e>         kgc:where   
210  SpeckledBand:365    kgc:infoSource   
321  SpeckledBand:388  kgc:hasPredicate   
386          <mask_e>       kgc:subject   
85   SpeckledBand:338    kgc:infoSource   
145  SpeckledBand:351       kgc:subject   
244  SpeckledBand:371  kgc:hasPredicate   
151  SpeckledBand:352         kgc:where   
284  SpeckledBand:379       kgc:subject   
364  SpeckledBand:398       kgc:subject   
24   SpeckledBand:326    kgc:infoSource   
309  SpeckledBand:385  kgc:hasPredicate   
326  SpeckledBand:389            kgc:to   
352  SpeckledBand:395          kgc:time   
106  SpeckledBand:343         kgc:where   
125  SpeckledBand:347         kgc:where   
329  SpeckledBand:390       kgc:subject   
89   SpeckledBand:339       kgc:subject   
87   SpeckledBand:338          kgc:time   
263  SpeckledBand:375  kgc:hasPredicate   
181  SpeckledBand:359  kgc:hasPredicate   
325  SpeckledBand:389  kgc:hasPredicate   
371  SpeckledBand:399  kgc:hasPredicate   
158  SpeckledBand:354  kgc:hasPredicate   
206  SpeckledBand:364          kgc:time   
370  SpeckledBand:399       kgc:subject   
46   SpeckledBand:330          kgc:time   
51   SpeckledBand:331          kgc:time   
139  SpeckledBand:350       kgc:subject   
103  SpeckledBand:341          kgc:time   
204  SpeckledBand:364    kgc:infoSource   
265  SpeckledBand:375    kgc:infoSource   
186  SpeckledBand:360            kgc:to   
257  SpeckledBand:374       kgc:subject   
212  SpeckledBand:365          kgc:time   
34   SpeckledBand:328       kgc:subject   
331  SpeckledBand:390         kgc:where   
255  SpeckledBand:373          kgc:time   
32   SpeckledBand:327          kgc:time   
100  SpeckledBand:341  kgc:hasPredicate   
187  SpeckledBand:360          kgc:time   
163  SpeckledBand:355          kgc:time   
91   SpeckledBand:339    kgc:infoSource   
132  SpeckledBand:348          kgc:time   
376  SpeckledBand:400  kgc:hasPredicate   
93   SpeckledBand:339          kgc:time   
116  SpeckledBand:345          kgc:time   
195  SpeckledBand:362  kgc:hasPredicate   
69   SpeckledBand:335       kgc:subject   
78   SpeckledBand:336          kgc:time   
156  SpeckledBand:353          kgc:time   
76   SpeckledBand:336  kgc:hasPredicate   
202  SpeckledBand:364       kgc:subject   
292  SpeckledBand:

### DevilsFoot(悪魔の足跡１)
Who killed the victims? (criminal & explanation)
被害者: Brenda
犯人: Mortimer
犯行動機: 財産

In [19]:
def do_devil1_pred():
    title = 'DevilsFoot'
    victim_name = 'Brenda'
    killer_name = 'Mortimer'
    last_index = 489
    story_len = 80
    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_devil1_pred()
pass

2023-02-05 09:46:02 - INFO - 3696358453.py - 13 - The pred ranking about DevilsFoot:Mortimer is 3


predicate  \
ranking                                      
0                          AllTitle:Holmes   
1                      word.predicate:kill   
2                     word.predicate:guess   
3                      word.predicate:come   
4                   word.predicate:notWant   
5                       word.predicate:die   
6                       SilverBlaze:police   
7                    DancingMen:Abe_Slaney   
8                   word.predicate:notHave   
9                                  <bos_e>   
10                  ACaseOfIdentity:Hosmer   
11                    DevilsFoot:Sterndale   
12                     word.predicate:hold   
13        SilverBlaze:Wife_of_John_Straker   
14                     DevilsFoot:telegram   
15                   SpeckledBand:corridor   
16                  word.predicate:request   
17                         AllTitle:Watson   
18                     word.predicate:send   
19       DevilsFoot:cottage_of_Pordeux_Bay   

                                          whom  \
ranking                                          
0                            DevilsFoot:Brenda   
1                          DevilsFoot:Mortimer   
2                              AllTitle:Holmes   
3                  ResidentPatient:Blessington   
4                            DevilsFoot:George   
5                         DevilsFoot:Sterndale   
6                              AllTitle:Watson   
7               SpeckledBand:Roylott_s_bedroom   
8                           SpeckledBand:Julia   
9                      word.predicate:notExist   
10                            CrookedMan:Henry   
11                           DevilsFoot:window   
12          ResidentPatient:Brook_Street_house   
13                        word.predicate:exist   
14                         word.predicate:fire   
15                      ACaseOfIdentity:Hosmer   
16                         word.predicate:talk   
17                DateTime:1898-08-13T03:02:00   
18       AbbeyGrange:Burglary_team_of_Lewisham   
19                      word.predicate:receive   

                                subject  \
ranking                                   
0                               <bos_e>   
1                       AllTitle:Holmes   
2                       AllTitle:Watson   
3                   DevilsFoot:Mortimer   
4                  DevilsFoot:Sterndale   
5               word.predicate:notExist   
6                  word.predicate:write   
7                ACaseOfIdentity:Hosmer   
8                    SpeckledBand:Helen   
9                  word.predicate:exist   
10                   word.predicate:say   
11       SpeckledBand:Roylott_s_bedroom   
12                    DevilsFoot:George   
13                    DevilsFoot:window   
14                  word.predicate:meet   
15                 word.predicate:guess   
16               word.predicate:notHave   
17          ResidentPatient:Blessington   
18              SilverBlaze:Silas_Brown   
19                 word.predicate:close   

                                            why  \
ranking                                           
0                                       <bos_e>   
1                               AllTitle:Holmes   
2                       word.predicate:notExist   
3                               AllTitle:Watson   
4                           DevilsFoot:Mortimer   
5                          DevilsFoot:Sterndale   
6                        ACaseOfIdentity:Hosmer   
7                    ResidentPatient:Helper_boy   
8                           word.predicate:meet   
9                         DancingMen:Abe_Slaney   
10              ResidentPatient:Percy_Trevelyan   
11                          word.predicate:dead   
12                 DateTime:1883-04-01T10:00:00   
13                            DevilsFoot:Brenda   
14       AbbeyGrange:Thought_of_Stanley_Hopkins   
15                     SilverBlaze:Edith_Baxter   
16                  ResidentPatient:Blessington   
17 

index=358, triple=['DevilsFoot:489', 'kgc:hasPredicate', 'word.predicate:find'], attention list


head          relation  \
351  DevilsFoot:487   kgc:hasProperty   
305  DevilsFoot:475   kgc:hasProperty   
334  DevilsFoot:482            kgc:to   
151  DevilsFoot:441   kgc:hasProperty   
139  DevilsFoot:439            kgc:to   
329  DevilsFoot:481          kgc:from   
301  DevilsFoot:474   kgc:hasProperty   
125  DevilsFoot:436   kgc:hasProperty   
213  DevilsFoot:455          kgc:whom   
210  DevilsFoot:454            kgc:to   
361        <mask_e>    kgc:infoSource   
48   DevilsFoot:418          kgc:time   
284  DevilsFoot:472    kgc:infoSource   
214  DevilsFoot:455    kgc:infoSource   
335  DevilsFoot:482    kgc:infoSource   
352  DevilsFoot:487            kgc:on   
328  DevilsFoot:481    kgc:infoSource   
357  DevilsFoot:489       kgc:subject   
252  DevilsFoot:464    kgc:infoSource   
169  DevilsFoot:445          kgc:whom   
228  DevilsFoot:459           kgc:why   
232  DevilsFoot:460    kgc:infoSource   
278  DevilsFoot:471    kgc:infoSource   
5    DevilsFoot:411    kgc:infoSource   
268  DevilsFoot:469    kgc:infoSource   
3    DevilsFoot:410    kgc:infoSource   
348  DevilsFoot:486    kgc:infoSource   
344  DevilsFoot:485    kgc:infoSource   
363        <mask_e>          kgc:whom   
170  DevilsFoot:445    kgc:infoSource   
143  DevilsFoot:439          kgc:time   
52   DevilsFoot:419    kgc:infoSource   
157  DevilsFoot:442    kgc:infoSource   
260  DevilsFoot:467    kgc:infoSource   
109  DevilsFoot:433       kgc:subject   
131  DevilsFoot:437          kgc:whom   
264  DevilsFoot:468    kgc:infoSource   
224  DevilsFoot:458    kgc:infoSource   
227  DevilsFoot:459  kgc:hasPredicate   
216  DevilsFoot:456    kgc:infoSource   
318  DevilsFoot:478    kgc:infoSource   
53   DevilsFoot:419           kgc:why   
302  DevilsFoot:474    kgc:infoSource   
271  DevilsFoot:470    kgc:infoSource   
247  DevilsFoot:463    kgc:infoSource   
355  DevilsFoot:488         kgc:where   
280  DevilsFoot:472       kgc:subject   
25   DevilsFoot:413    kgc:infoSource   
237  DevilsFoot:461    kgc:infoSource   
256  DevilsFoot:466       kgc:subject   
189  DevilsFoot:448    kgc:infoSource   
37   DevilsFoot:416          kgc:whom   
152  DevilsFoot:441    kgc:infoSource   
354  DevilsFoot:488       kgc:subject   
230  DevilsFoot:460       kgc:subject   
218  DevilsFoot:457       kgc:subject   
341  DevilsFoot:484         kgc:where   
337  DevilsFoot:483       kgc:subject   
241  DevilsFoot:462    kgc:infoSource   
254  DevilsFoot:465       kgc:subject   
193  DevilsFoot:449    kgc:infoSource   
262  DevilsFoot:468       kgc:subject   
107  DevilsFoot:432       kgc:subject   
306  DevilsFoot:475    kgc:infoSource   
236  DevilsFoot:461          kgc:whom   
347  DevilsFoot:486  kgc:hasPredicate   
283  DevilsFoot:472          kgc:whom   
350  DevilsFoot:487       kgc:subject   
181  DevilsFoot:446    kgc:infoSource   
156  DevilsFoot:442          kgc:whom   
212  DevilsFoot:455  kgc:hasPredicate   
266  DevilsFoot:469       kgc:subject   
331  DevilsFoot:482       kgc:subject   
323  DevilsFoot:480       kgc:subject   
320  DevilsFoot:479       kgc:subject   
362        <mask_e>  kgc:hasPredicate   
208  DevilsFoot:454       kgc:subject   
165  DevilsFoot:444    kgc:infoSource   
197  DevilsFoot:451       kgc:subject   
159  DevilsFoot:443       kgc:subject   
304  DevilsFoot:475       kgc:subject   
220  DevilsFoot:457    kgc:infoSource   
43   DevilsFoot:418       kgc:subject   
315  DevilsFoot:477    kgc:infoSource   
226  DevilsFoot:459       kgc:subject   
250  DevilsFoot:464  kgc:hasPredicate   
126  DevilsFoot:436    kgc:infoSource   
326  DevilsFoot:481       kgc:subject   
300  DevilsFoot:474       kgc:subject   
249  DevilsFoot:464       kgc:subject   
34   DevilsFoot:415    kgc:infoSource   
1    DevilsFoot:410       kgc:subject   
50   DevilsFoot:419       kgc:subject   
202  DevilsFoot:452       kgc:subject   
286  DevilsFoot:473       kgc:subject   
270  DevilsFoot:470       kgc:subject   
199  DevilsFoot:451         kgc:where 

index=359, triple=['DevilsFoot:489', 'kgc:what', 'DevilsFoot:gravel'], attention list


...

head          relation  \
352  DevilsFoot:487            kgc:on   
227  DevilsFoot:459  kgc:hasPredicate   
169  DevilsFoot:445          kgc:whom   
168  DevilsFoot:445  kgc:hasPredicate   
362        <mask_e>  kgc:hasPredicate   
2    DevilsFoot:410  kgc:hasPredicate   
170  DevilsFoot:445    kgc:infoSource   
212  DevilsFoot:455  kgc:hasPredicate   
351  DevilsFoot:487   kgc:hasProperty   
358  DevilsFoot:489  kgc:hasPredicate   
321  DevilsFoot:479  kgc:hasPredicate   
343  DevilsFoot:485  kgc:hasPredicate   
100  DevilsFoot:430  kgc:hasPredicate   
154  DevilsFoot:442  kgc:hasPredicate   
250  DevilsFoot:464  kgc:hasPredicate   
104  DevilsFoot:431  kgc:hasPredicate   
44   DevilsFoot:418  kgc:hasPredicate   
146  DevilsFoot:440  kgc:hasPredicate   
214  DevilsFoot:455    kgc:infoSource   
163  DevilsFoot:444  kgc:hasPredicate   
133  DevilsFoot:438  kgc:hasPredicate   
138  DevilsFoot:439  kgc:hasPredicate   
347  DevilsFoot:486  kgc:hasPredicate   
314  DevilsFoot:477  kgc:hasPredicate   
129  DevilsFoot:437  kgc:hasPredicate   
165  DevilsFoot:444    kgc:infoSource   
95   DevilsFoot:429  kgc:hasPredicate   
157  DevilsFoot:442    kgc:infoSource   
52   DevilsFoot:419    kgc:infoSource   
209  DevilsFoot:454  kgc:hasPredicate   
344  DevilsFoot:485    kgc:infoSource   
119  DevilsFoot:435  kgc:hasPredicate   
259  DevilsFoot:467  kgc:hasPredicate   
260  DevilsFoot:467    kgc:infoSource   
338  DevilsFoot:483  kgc:hasPredicate   
51   DevilsFoot:419  kgc:hasPredicate   
263  DevilsFoot:468  kgc:hasPredicate   
247  DevilsFoot:463    kgc:infoSource   
264  DevilsFoot:468    kgc:infoSource   
39   DevilsFoot:417  kgc:hasPredicate   
173  DevilsFoot:446  kgc:hasPredicate   
348  DevilsFoot:486    kgc:infoSource   
284  DevilsFoot:472    kgc:infoSource   
327  DevilsFoot:481  kgc:hasPredicate   
274  DevilsFoot:471  kgc:hasPredicate   
328  DevilsFoot:481    kgc:infoSource   
219  DevilsFoot:457  kgc:hasPredicate   
235  DevilsFoot:461  kgc:hasPredicate   
252  DevilsFoot:464    kgc:infoSource   
25   DevilsFoot:413    kgc:infoSource   
216  DevilsFoot:456    kgc:infoSource   
110  DevilsFoot:433  kgc:hasPredicate   
152  DevilsFoot:441    kgc:infoSource   
306  DevilsFoot:475    kgc:infoSource   
232  DevilsFoot:460    kgc:infoSource   
48   DevilsFoot:418          kgc:time   
302  DevilsFoot:474    kgc:infoSource   
114  DevilsFoot:434  kgc:hasPredicate   
244  DevilsFoot:463  kgc:hasPredicate   
86   DevilsFoot:426          kgc:whom   
268  DevilsFoot:469    kgc:infoSource   
278  DevilsFoot:471    kgc:infoSource   
224  DevilsFoot:458    kgc:infoSource   
332  DevilsFoot:482  kgc:hasPredicate   
318  DevilsFoot:478    kgc:infoSource   
315  DevilsFoot:477    kgc:infoSource   
181  DevilsFoot:446    kgc:infoSource   
239  DevilsFoot:462  kgc:hasPredicate   
305  DevilsFoot:475   kgc:hasProperty   
23   DevilsFoot:413  kgc:hasPredicate   
213  DevilsFoot:455          kgc:whom   
361        <mask_e>    kgc:infoSource   
88   DevilsFoot:427  kgc:hasPredicate   
8    DevilsFoot:412  kgc:hasPredicate   
271  DevilsFoot:470    kgc:infoSource   
228  DevilsFoot:459           kgc:why   
117  DevilsFoot:434    kgc:infoSource   
156  DevilsFoot:442          kgc:whom   
335  DevilsFoot:482    kgc:infoSource   
220  DevilsFoot:457    kgc:infoSource   
97   DevilsFoot:429            kgc:on   
203  DevilsFoot:452  kgc:hasPredicate   
198  DevilsFoot:451  kgc:hasPredicate   
148  DevilsFoot:440    kgc:infoSource   
340  DevilsFoot:484  kgc:hasPredicate   
281  DevilsFoot:472  kgc:hasPredicate   
91   DevilsFoot:428  kgc:hasPredicate   
126  DevilsFoot:436    kgc:infoSource   
280  DevilsFoot:472       kgc:subject   
210  DevilsFoot:454            kgc:to   
283  DevilsFoot:472          kgc:whom   
29   DevilsFoot:414    kgc:infoSource   
262  DevilsFoot:468       kgc:subject   
140  DevilsFoot:439    kgc:infoSource   
45   DevilsFoot:418    kgc:infoSource   
241  DevilsFoot:462    kgc:infoSource   
189  DevilsFoot:448    kgc:infoSource 

index=366, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
235  DevilsFoot:461  kgc:hasPredicate   
95   DevilsFoot:429  kgc:hasPredicate   
352  DevilsFoot:487            kgc:on   
170  DevilsFoot:445    kgc:infoSource   
52   DevilsFoot:419    kgc:infoSource   
351  DevilsFoot:487   kgc:hasProperty   
214  DevilsFoot:455    kgc:infoSource   
168  DevilsFoot:445  kgc:hasPredicate   
173  DevilsFoot:446  kgc:hasPredicate   
157  DevilsFoot:442    kgc:infoSource   
169  DevilsFoot:445          kgc:whom   
341  DevilsFoot:484         kgc:where   
154  DevilsFoot:442  kgc:hasPredicate   
239  DevilsFoot:462  kgc:hasPredicate   
361        <mask_e>    kgc:infoSource   
348  DevilsFoot:486    kgc:infoSource   
23   DevilsFoot:413  kgc:hasPredicate   
344  DevilsFoot:485    kgc:infoSource   
152  DevilsFoot:441    kgc:infoSource   
165  DevilsFoot:444    kgc:infoSource   
216  DevilsFoot:456    kgc:infoSource   
328  DevilsFoot:481    kgc:infoSource   
260  DevilsFoot:467    kgc:infoSource   
263  DevilsFoot:468  kgc:hasPredicate   
213  DevilsFoot:455          kgc:whom   
281  DevilsFoot:472  kgc:hasPredicate   
306  DevilsFoot:475    kgc:infoSource   
355  DevilsFoot:488         kgc:where   
358  DevilsFoot:489  kgc:hasPredicate   
274  DevilsFoot:471  kgc:hasPredicate   
232  DevilsFoot:460    kgc:infoSource   
45   DevilsFoot:418    kgc:infoSource   
181  DevilsFoot:446    kgc:infoSource   
39   DevilsFoot:417  kgc:hasPredicate   
224  DevilsFoot:458    kgc:infoSource   
25   DevilsFoot:413    kgc:infoSource   
264  DevilsFoot:468    kgc:infoSource   
48   DevilsFoot:418          kgc:time   
244  DevilsFoot:463  kgc:hasPredicate   
220  DevilsFoot:457    kgc:infoSource   
119  DevilsFoot:435  kgc:hasPredicate   
193  DevilsFoot:449    kgc:infoSource   
318  DevilsFoot:478    kgc:infoSource   
302  DevilsFoot:474    kgc:infoSource   
203  DevilsFoot:452  kgc:hasPredicate   
91   DevilsFoot:428  kgc:hasPredicate   
227  DevilsFoot:459  kgc:hasPredicate   
156  DevilsFoot:442          kgc:whom   
189  DevilsFoot:448    kgc:infoSource   
335  DevilsFoot:482    kgc:infoSource   
343  DevilsFoot:485  kgc:hasPredicate   
237  DevilsFoot:461    kgc:infoSource   
247  DevilsFoot:463    kgc:infoSource   
146  DevilsFoot:440  kgc:hasPredicate   
241  DevilsFoot:462    kgc:infoSource   
284  DevilsFoot:472    kgc:infoSource   
278  DevilsFoot:471    kgc:infoSource   
148  DevilsFoot:440    kgc:infoSource   
133  DevilsFoot:438  kgc:hasPredicate   
29   DevilsFoot:414    kgc:infoSource   
315  DevilsFoot:477    kgc:infoSource   
347  DevilsFoot:486  kgc:hasPredicate   
250  DevilsFoot:464  kgc:hasPredicate   
311  DevilsFoot:476    kgc:infoSource   
268  DevilsFoot:469    kgc:infoSource   
41   DevilsFoot:417    kgc:infoSource   
88   DevilsFoot:427  kgc:hasPredicate   
252  DevilsFoot:464    kgc:infoSource   
163  DevilsFoot:444  kgc:hasPredicate   
34   DevilsFoot:415    kgc:infoSource   
212  DevilsFoot:455  kgc:hasPredicate   
138  DevilsFoot:439  kgc:hasPredicate   
44   DevilsFoot:418  kgc:hasPredicate   
2    DevilsFoot:410  kgc:hasPredicate   
271  DevilsFoot:470    kgc:infoSource   
354  DevilsFoot:488       kgc:subject   
199  DevilsFoot:451         kgc:where   
114  DevilsFoot:434  kgc:hasPredicate   
3    DevilsFoot:410    kgc:infoSource   
329  DevilsFoot:481          kgc:from   
210  DevilsFoot:454            kgc:to   
8    DevilsFoot:412  kgc:hasPredicate   
140  DevilsFoot:439    kgc:infoSource   
362        <mask_e>  kgc:hasPredicate   
56   DevilsFoot:420  kgc:hasPredicate   
129  DevilsFoot:437  kgc:hasPredicate   
126  DevilsFoot:436    kgc:infoSource   
338  DevilsFoot:483  kgc:hasPredicate   
32   DevilsFoot:415  kgc:hasPredicate   
117  DevilsFoot:434    kgc:infoSource   
50   DevilsFoot:419       kgc:subject   
259  DevilsFoot:467  kgc:hasPredicate   
321  DevilsFoot:479  kgc:hasPredicate   
363        <mask_e>          kgc:whom   
327  DevilsFoot:481  kgc:hasPredicate   
79   DevilsFoot:424    kgc:infoSource   
357  DevilsFoot:489       kgc:subject 

index=367, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
352  DevilsFoot:487            kgc:on   
341  DevilsFoot:484         kgc:where   
355  DevilsFoot:488         kgc:where   
351  DevilsFoot:487   kgc:hasProperty   
214  DevilsFoot:455    kgc:infoSource   
199  DevilsFoot:451         kgc:where   
52   DevilsFoot:419    kgc:infoSource   
111  DevilsFoot:433         kgc:where   
344  DevilsFoot:485    kgc:infoSource   
348  DevilsFoot:486    kgc:infoSource   
170  DevilsFoot:445    kgc:infoSource   
152  DevilsFoot:441    kgc:infoSource   
361        <mask_e>    kgc:infoSource   
157  DevilsFoot:442    kgc:infoSource   
213  DevilsFoot:455          kgc:whom   
216  DevilsFoot:456    kgc:infoSource   
328  DevilsFoot:481    kgc:infoSource   
306  DevilsFoot:475    kgc:infoSource   
169  DevilsFoot:445          kgc:whom   
263  DevilsFoot:468  kgc:hasPredicate   
260  DevilsFoot:467    kgc:infoSource   
302  DevilsFoot:474    kgc:infoSource   
33   DevilsFoot:415         kgc:where   
335  DevilsFoot:482    kgc:infoSource   
318  DevilsFoot:478    kgc:infoSource   
165  DevilsFoot:444    kgc:infoSource   
264  DevilsFoot:468    kgc:infoSource   
120  DevilsFoot:435         kgc:where   
232  DevilsFoot:460    kgc:infoSource   
45   DevilsFoot:418    kgc:infoSource   
25   DevilsFoot:413    kgc:infoSource   
284  DevilsFoot:472    kgc:infoSource   
224  DevilsFoot:458    kgc:infoSource   
181  DevilsFoot:446    kgc:infoSource   
212  DevilsFoot:455  kgc:hasPredicate   
252  DevilsFoot:464    kgc:infoSource   
220  DevilsFoot:457    kgc:infoSource   
48   DevilsFoot:418          kgc:time   
315  DevilsFoot:477    kgc:infoSource   
354  DevilsFoot:488       kgc:subject   
140  DevilsFoot:439    kgc:infoSource   
29   DevilsFoot:414    kgc:infoSource   
247  DevilsFoot:463    kgc:infoSource   
278  DevilsFoot:471    kgc:infoSource   
268  DevilsFoot:469    kgc:infoSource   
126  DevilsFoot:436    kgc:infoSource   
210  DevilsFoot:454            kgc:to   
271  DevilsFoot:470    kgc:infoSource   
148  DevilsFoot:440    kgc:infoSource   
32   DevilsFoot:415  kgc:hasPredicate   
34   DevilsFoot:415    kgc:infoSource   
340  DevilsFoot:484  kgc:hasPredicate   
189  DevilsFoot:448    kgc:infoSource   
311  DevilsFoot:476    kgc:infoSource   
193  DevilsFoot:449    kgc:infoSource   
117  DevilsFoot:434    kgc:infoSource   
262  DevilsFoot:468       kgc:subject   
79   DevilsFoot:424    kgc:infoSource   
192  DevilsFoot:449         kgc:where   
50   DevilsFoot:419       kgc:subject   
41   DevilsFoot:417    kgc:infoSource   
219  DevilsFoot:457  kgc:hasPredicate   
357  DevilsFoot:489       kgc:subject   
114  DevilsFoot:434  kgc:hasPredicate   
237  DevilsFoot:461    kgc:infoSource   
337  DevilsFoot:483       kgc:subject   
3    DevilsFoot:410    kgc:infoSource   
329  DevilsFoot:481          kgc:from   
168  DevilsFoot:445  kgc:hasPredicate   
367        <mask_e>         kgc:where   
133  DevilsFoot:438  kgc:hasPredicate   
280  DevilsFoot:472       kgc:subject   
227  DevilsFoot:459  kgc:hasPredicate   
75   DevilsFoot:423    kgc:infoSource   
304  DevilsFoot:475       kgc:subject   
86   DevilsFoot:426          kgc:whom   
338  DevilsFoot:483  kgc:hasPredicate   
156  DevilsFoot:442          kgc:whom   
95   DevilsFoot:429  kgc:hasPredicate   
362        <mask_e>  kgc:hasPredicate   
197  DevilsFoot:451       kgc:subject   
300  DevilsFoot:474       kgc:subject   
208  DevilsFoot:454       kgc:subject   
256  DevilsFoot:466       kgc:subject   
61   DevilsFoot:421    kgc:infoSource   
323  DevilsFoot:480       kgc:subject   
331  DevilsFoot:482       kgc:subject   
241  DevilsFoot:462    kgc:infoSource   
97   DevilsFoot:429            kgc:on   
159  DevilsFoot:443       kgc:subject   
172  DevilsFoot:446       kgc:subject   
266  DevilsFoot:469       kgc:subject   
281  DevilsFoot:472  kgc:hasPredicate   
23   DevilsFoot:413  kgc:hasPredicate   
334  DevilsFoot:482            kgc:to   
320  DevilsFoot:479       kgc:subject   
363        <mask_e>          kgc:whom 

### DevilsFoot(悪魔の足跡2)
Who killed the victims? (criminal & explanation)
被害者: Mortimer
犯人: 
犯行動機: 恋人の敵

In [20]:
def do_devil2_pred():
    title = 'DevilsFoot'
    victim_name = 'Mortimer'
    killer_name = 'Sterndale'
    last_index = 489
    story_len = 80
    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_devil2_pred()
pass

2023-02-05 09:46:03 - INFO - 3696358453.py - 13 - The pred ranking about DevilsFoot:Sterndale is 4


predicate  \
ranking                                      
0                      word.predicate:kill   
1                          AllTitle:Holmes   
2                     word.predicate:guess   
3                      word.predicate:come   
4                   word.predicate:notWant   
5                       word.predicate:die   
6                       SilverBlaze:police   
7                   word.predicate:notHave   
8                    DancingMen:Abe_Slaney   
9                                  <bos_e>   
10                  ACaseOfIdentity:Hosmer   
11                     word.predicate:hold   
12                   SpeckledBand:corridor   
13                   word.predicate:return   
14                    DevilsFoot:Sterndale   
15        SilverBlaze:Wife_of_John_Straker   
16                     word.predicate:send   
17                     DevilsFoot:telegram   
18       DevilsFoot:cottage_of_Pordeux_Bay   
19                  word.predicate:request   

                                          whom  \
ranking                                          
0                          DevilsFoot:Mortimer   
1                              AllTitle:Holmes   
2                      word.predicate:notExist   
3                              AllTitle:Watson   
4                   ResidentPatient:Helper_boy   
5                         word.predicate:write   
6                  ResidentPatient:Blessington   
7                                      <bos_e>   
8        AbbeyGrange:Burglary_team_of_Lewisham   
9                            DevilsFoot:George   
10                          word.predicate:say   
11                        word.predicate:exist   
12                         AbbeyGrange:Theresa   
13                          SpeckledBand:Julia   
14                      ACaseOfIdentity:Hosmer   
15                        word.predicate:guess   
16                 SilverBlaze:Fitzroy_Simpson   
17                         DevilsFoot:Roundhay   
18                DateTime:1881-04-01T00:00:00   
19                DateTime:1881-04-01T03:00:00   

                                subject                              why  \
ranking                                                                    
0                               <bos_e>                          <bos_e>   
1                   DevilsFoot:Mortimer                  AllTitle:Holmes   
2                       AllTitle:Holmes          word.predicate:notExist   
3                       AllTitle:Watson              DevilsFoot:Mortimer   
4                  DevilsFoot:Sterndale       ResidentPatient:Helper_boy   
5               word.predicate:notExist            DancingMen:Abe_Slaney   
6                  word.predicate:write           ACaseOfIdentity:Hosmer   
7                ACaseOfIdentity:Hosmer                DevilsFoot:Brenda   
8                    word.predicate:say                  AllTitle:Watson   
9                  word.predicate:exist         SilverBlaze:Edith_Baxter   
10          ResidentPatient:Blessington  ResidentPatient:Percy_Trevelyan   
11                 word.predicate:guess      ResidentPatient:Blessington   
12           ResidentPatient:Helper_boy             DevilsFoot:Sterndale   
13                    DevilsFoot:George              word.predicate:dead   
14                   SpeckledBand:Helen              word.predicate:meet   
15       SpeckledBand:Roylott_s_bedroom              DevilsFoot:Cornwall   
16                    DevilsFoot:window     DateTime:1883-04-01T10:00:00   
17                    DevilsFoot:Brenda              word.predicate:come   
18                  AbbeyGrange:Theresa                DevilsFoot:George   
19              SilverBlaze:Silas_Brown           word.predicate:believe   

                                           what  \
ranking                                           
0                                       <bos_e>   
1                               AllTitle:Holmes   
2                          DevilsFoot:Ster

index=358, triple=['DevilsFoot:489', 'kgc:hasPredicate', 'word.predicate:find'], attention list


head          relation  \
351  DevilsFoot:487   kgc:hasProperty   
305  DevilsFoot:475   kgc:hasProperty   
334  DevilsFoot:482            kgc:to   
151  DevilsFoot:441   kgc:hasProperty   
139  DevilsFoot:439            kgc:to   
329  DevilsFoot:481          kgc:from   
301  DevilsFoot:474   kgc:hasProperty   
125  DevilsFoot:436   kgc:hasProperty   
213  DevilsFoot:455          kgc:whom   
210  DevilsFoot:454            kgc:to   
361        <mask_e>    kgc:infoSource   
48   DevilsFoot:418          kgc:time   
284  DevilsFoot:472    kgc:infoSource   
214  DevilsFoot:455    kgc:infoSource   
335  DevilsFoot:482    kgc:infoSource   
352  DevilsFoot:487            kgc:on   
328  DevilsFoot:481    kgc:infoSource   
357  DevilsFoot:489       kgc:subject   
252  DevilsFoot:464    kgc:infoSource   
169  DevilsFoot:445          kgc:whom   
228  DevilsFoot:459           kgc:why   
5    DevilsFoot:411    kgc:infoSource   
278  DevilsFoot:471    kgc:infoSource   
232  DevilsFoot:460    kgc:infoSource   
3    DevilsFoot:410    kgc:infoSource   
348  DevilsFoot:486    kgc:infoSource   
344  DevilsFoot:485    kgc:infoSource   
268  DevilsFoot:469    kgc:infoSource   
143  DevilsFoot:439          kgc:time   
170  DevilsFoot:445    kgc:infoSource   
52   DevilsFoot:419    kgc:infoSource   
157  DevilsFoot:442    kgc:infoSource   
260  DevilsFoot:467    kgc:infoSource   
131  DevilsFoot:437          kgc:whom   
109  DevilsFoot:433       kgc:subject   
227  DevilsFoot:459  kgc:hasPredicate   
53   DevilsFoot:419           kgc:why   
318  DevilsFoot:478    kgc:infoSource   
264  DevilsFoot:468    kgc:infoSource   
224  DevilsFoot:458    kgc:infoSource   
216  DevilsFoot:456    kgc:infoSource   
302  DevilsFoot:474    kgc:infoSource   
355  DevilsFoot:488         kgc:where   
280  DevilsFoot:472       kgc:subject   
247  DevilsFoot:463    kgc:infoSource   
271  DevilsFoot:470    kgc:infoSource   
25   DevilsFoot:413    kgc:infoSource   
237  DevilsFoot:461    kgc:infoSource   
37   DevilsFoot:416          kgc:whom   
256  DevilsFoot:466       kgc:subject   
362        <mask_e>  kgc:hasPredicate   
189  DevilsFoot:448    kgc:infoSource   
218  DevilsFoot:457       kgc:subject   
152  DevilsFoot:441    kgc:infoSource   
354  DevilsFoot:488       kgc:subject   
230  DevilsFoot:460       kgc:subject   
341  DevilsFoot:484         kgc:where   
337  DevilsFoot:483       kgc:subject   
241  DevilsFoot:462    kgc:infoSource   
254  DevilsFoot:465       kgc:subject   
262  DevilsFoot:468       kgc:subject   
193  DevilsFoot:449    kgc:infoSource   
347  DevilsFoot:486  kgc:hasPredicate   
236  DevilsFoot:461          kgc:whom   
107  DevilsFoot:432       kgc:subject   
283  DevilsFoot:472          kgc:whom   
350  DevilsFoot:487       kgc:subject   
306  DevilsFoot:475    kgc:infoSource   
156  DevilsFoot:442          kgc:whom   
212  DevilsFoot:455  kgc:hasPredicate   
181  DevilsFoot:446    kgc:infoSource   
331  DevilsFoot:482       kgc:subject   
323  DevilsFoot:480       kgc:subject   
266  DevilsFoot:469       kgc:subject   
320  DevilsFoot:479       kgc:subject   
208  DevilsFoot:454       kgc:subject   
165  DevilsFoot:444    kgc:infoSource   
43   DevilsFoot:418       kgc:subject   
159  DevilsFoot:443       kgc:subject   
304  DevilsFoot:475       kgc:subject   
197  DevilsFoot:451       kgc:subject   
250  DevilsFoot:464  kgc:hasPredicate   
326  DevilsFoot:481       kgc:subject   
315  DevilsFoot:477    kgc:infoSource   
226  DevilsFoot:459       kgc:subject   
220  DevilsFoot:457    kgc:infoSource   
249  DevilsFoot:464       kgc:subject   
126  DevilsFoot:436    kgc:infoSource   
300  DevilsFoot:474       kgc:subject   
1    DevilsFoot:410       kgc:subject   
34   DevilsFoot:415    kgc:infoSource   
50   DevilsFoot:419       kgc:subject   
286  DevilsFoot:473       kgc:subject   
202  DevilsFoot:452       kgc:subject   
270  DevilsFoot:470       kgc:subject   
29   DevilsFoot:414    kgc:infoSource   
140  DevilsFoot:439    kgc:infoSource 

index=359, triple=['DevilsFoot:489', 'kgc:what', 'DevilsFoot:gravel'], attention list


...

head          relation  \
352  DevilsFoot:487            kgc:on   
169  DevilsFoot:445          kgc:whom   
351  DevilsFoot:487   kgc:hasProperty   
227  DevilsFoot:459  kgc:hasPredicate   
168  DevilsFoot:445  kgc:hasPredicate   
170  DevilsFoot:445    kgc:infoSource   
305  DevilsFoot:475   kgc:hasProperty   
362        <mask_e>  kgc:hasPredicate   
343  DevilsFoot:485  kgc:hasPredicate   
212  DevilsFoot:455  kgc:hasPredicate   
321  DevilsFoot:479  kgc:hasPredicate   
100  DevilsFoot:430  kgc:hasPredicate   
163  DevilsFoot:444  kgc:hasPredicate   
347  DevilsFoot:486  kgc:hasPredicate   
154  DevilsFoot:442  kgc:hasPredicate   
301  DevilsFoot:474   kgc:hasProperty   
2    DevilsFoot:410  kgc:hasPredicate   
214  DevilsFoot:455    kgc:infoSource   
104  DevilsFoot:431  kgc:hasPredicate   
314  DevilsFoot:477  kgc:hasPredicate   
44   DevilsFoot:418  kgc:hasPredicate   
358  DevilsFoot:489  kgc:hasPredicate   
250  DevilsFoot:464  kgc:hasPredicate   
48   DevilsFoot:418          kgc:time   
327  DevilsFoot:481  kgc:hasPredicate   
284  DevilsFoot:472    kgc:infoSource   
247  DevilsFoot:463    kgc:infoSource   
209  DevilsFoot:454  kgc:hasPredicate   
146  DevilsFoot:440  kgc:hasPredicate   
165  DevilsFoot:444    kgc:infoSource   
157  DevilsFoot:442    kgc:infoSource   
133  DevilsFoot:438  kgc:hasPredicate   
52   DevilsFoot:419    kgc:infoSource   
259  DevilsFoot:467  kgc:hasPredicate   
344  DevilsFoot:485    kgc:infoSource   
328  DevilsFoot:481    kgc:infoSource   
260  DevilsFoot:467    kgc:infoSource   
51   DevilsFoot:419  kgc:hasPredicate   
348  DevilsFoot:486    kgc:infoSource   
138  DevilsFoot:439  kgc:hasPredicate   
264  DevilsFoot:468    kgc:infoSource   
252  DevilsFoot:464    kgc:infoSource   
129  DevilsFoot:437  kgc:hasPredicate   
119  DevilsFoot:435  kgc:hasPredicate   
219  DevilsFoot:457  kgc:hasPredicate   
86   DevilsFoot:426          kgc:whom   
338  DevilsFoot:483  kgc:hasPredicate   
25   DevilsFoot:413    kgc:infoSource   
302  DevilsFoot:474    kgc:infoSource   
263  DevilsFoot:468  kgc:hasPredicate   
232  DevilsFoot:460    kgc:infoSource   
235  DevilsFoot:461  kgc:hasPredicate   
39   DevilsFoot:417  kgc:hasPredicate   
173  DevilsFoot:446  kgc:hasPredicate   
306  DevilsFoot:475    kgc:infoSource   
213  DevilsFoot:455          kgc:whom   
156  DevilsFoot:442          kgc:whom   
278  DevilsFoot:471    kgc:infoSource   
95   DevilsFoot:429  kgc:hasPredicate   
315  DevilsFoot:477    kgc:infoSource   
216  DevilsFoot:456    kgc:infoSource   
274  DevilsFoot:471  kgc:hasPredicate   
152  DevilsFoot:441    kgc:infoSource   
318  DevilsFoot:478    kgc:infoSource   
228  DevilsFoot:459           kgc:why   
110  DevilsFoot:433  kgc:hasPredicate   
268  DevilsFoot:469    kgc:infoSource   
224  DevilsFoot:458    kgc:infoSource   
283  DevilsFoot:472          kgc:whom   
244  DevilsFoot:463  kgc:hasPredicate   
159  DevilsFoot:443       kgc:subject   
181  DevilsFoot:446    kgc:infoSource   
114  DevilsFoot:434  kgc:hasPredicate   
239  DevilsFoot:462  kgc:hasPredicate   
332  DevilsFoot:482  kgc:hasPredicate   
97   DevilsFoot:429            kgc:on   
280  DevilsFoot:472       kgc:subject   
335  DevilsFoot:482    kgc:infoSource   
271  DevilsFoot:470    kgc:infoSource   
262  DevilsFoot:468       kgc:subject   
304  DevilsFoot:475       kgc:subject   
300  DevilsFoot:474       kgc:subject   
210  DevilsFoot:454            kgc:to   
361        <mask_e>    kgc:infoSource   
117  DevilsFoot:434    kgc:infoSource   
126  DevilsFoot:436    kgc:infoSource   
256  DevilsFoot:466       kgc:subject   
167  DevilsFoot:445       kgc:subject   
203  DevilsFoot:452  kgc:hasPredicate   
140  DevilsFoot:439    kgc:infoSource   
286  DevilsFoot:473       kgc:subject   
148  DevilsFoot:440    kgc:infoSource   
220  DevilsFoot:457    kgc:infoSource   
266  DevilsFoot:469       kgc:subject   
53   DevilsFoot:419           kgc:why   
329  DevilsFoot:481          kgc:from   
340  DevilsFoot:484  kgc:hasPredicate 

index=366, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
235  DevilsFoot:461  kgc:hasPredicate   
351  DevilsFoot:487   kgc:hasProperty   
352  DevilsFoot:487            kgc:on   
170  DevilsFoot:445    kgc:infoSource   
95   DevilsFoot:429  kgc:hasPredicate   
52   DevilsFoot:419    kgc:infoSource   
214  DevilsFoot:455    kgc:infoSource   
169  DevilsFoot:445          kgc:whom   
157  DevilsFoot:442    kgc:infoSource   
168  DevilsFoot:445  kgc:hasPredicate   
341  DevilsFoot:484         kgc:where   
239  DevilsFoot:462  kgc:hasPredicate   
348  DevilsFoot:486    kgc:infoSource   
152  DevilsFoot:441    kgc:infoSource   
154  DevilsFoot:442  kgc:hasPredicate   
344  DevilsFoot:485    kgc:infoSource   
165  DevilsFoot:444    kgc:infoSource   
173  DevilsFoot:446  kgc:hasPredicate   
263  DevilsFoot:468  kgc:hasPredicate   
216  DevilsFoot:456    kgc:infoSource   
328  DevilsFoot:481    kgc:infoSource   
361        <mask_e>    kgc:infoSource   
355  DevilsFoot:488         kgc:where   
23   DevilsFoot:413  kgc:hasPredicate   
213  DevilsFoot:455          kgc:whom   
306  DevilsFoot:475    kgc:infoSource   
260  DevilsFoot:467    kgc:infoSource   
227  DevilsFoot:459  kgc:hasPredicate   
274  DevilsFoot:471  kgc:hasPredicate   
45   DevilsFoot:418    kgc:infoSource   
232  DevilsFoot:460    kgc:infoSource   
181  DevilsFoot:446    kgc:infoSource   
48   DevilsFoot:418          kgc:time   
25   DevilsFoot:413    kgc:infoSource   
224  DevilsFoot:458    kgc:infoSource   
343  DevilsFoot:485  kgc:hasPredicate   
119  DevilsFoot:435  kgc:hasPredicate   
347  DevilsFoot:486  kgc:hasPredicate   
156  DevilsFoot:442          kgc:whom   
193  DevilsFoot:449    kgc:infoSource   
244  DevilsFoot:463  kgc:hasPredicate   
264  DevilsFoot:468    kgc:infoSource   
302  DevilsFoot:474    kgc:infoSource   
358  DevilsFoot:489  kgc:hasPredicate   
281  DevilsFoot:472  kgc:hasPredicate   
220  DevilsFoot:457    kgc:infoSource   
318  DevilsFoot:478    kgc:infoSource   
237  DevilsFoot:461    kgc:infoSource   
247  DevilsFoot:463    kgc:infoSource   
138  DevilsFoot:439  kgc:hasPredicate   
91   DevilsFoot:428  kgc:hasPredicate   
335  DevilsFoot:482    kgc:infoSource   
146  DevilsFoot:440  kgc:hasPredicate   
189  DevilsFoot:448    kgc:infoSource   
284  DevilsFoot:472    kgc:infoSource   
241  DevilsFoot:462    kgc:infoSource   
278  DevilsFoot:471    kgc:infoSource   
148  DevilsFoot:440    kgc:infoSource   
44   DevilsFoot:418  kgc:hasPredicate   
315  DevilsFoot:477    kgc:infoSource   
29   DevilsFoot:414    kgc:infoSource   
133  DevilsFoot:438  kgc:hasPredicate   
212  DevilsFoot:455  kgc:hasPredicate   
39   DevilsFoot:417  kgc:hasPredicate   
250  DevilsFoot:464  kgc:hasPredicate   
362        <mask_e>  kgc:hasPredicate   
311  DevilsFoot:476    kgc:infoSource   
41   DevilsFoot:417    kgc:infoSource   
321  DevilsFoot:479  kgc:hasPredicate   
88   DevilsFoot:427  kgc:hasPredicate   
354  DevilsFoot:488       kgc:subject   
203  DevilsFoot:452  kgc:hasPredicate   
252  DevilsFoot:464    kgc:infoSource   
2    DevilsFoot:410  kgc:hasPredicate   
163  DevilsFoot:444  kgc:hasPredicate   
314  DevilsFoot:477  kgc:hasPredicate   
268  DevilsFoot:469    kgc:infoSource   
34   DevilsFoot:415    kgc:infoSource   
114  DevilsFoot:434  kgc:hasPredicate   
338  DevilsFoot:483  kgc:hasPredicate   
259  DevilsFoot:467  kgc:hasPredicate   
332  DevilsFoot:482  kgc:hasPredicate   
32   DevilsFoot:415  kgc:hasPredicate   
199  DevilsFoot:451         kgc:where   
271  DevilsFoot:470    kgc:infoSource   
140  DevilsFoot:439    kgc:infoSource   
363        <mask_e>          kgc:whom   
126  DevilsFoot:436    kgc:infoSource   
129  DevilsFoot:437  kgc:hasPredicate   
50   DevilsFoot:419       kgc:subject   
329  DevilsFoot:481          kgc:from   
219  DevilsFoot:457  kgc:hasPredicate   
327  DevilsFoot:481  kgc:hasPredicate   
3    DevilsFoot:410    kgc:infoSource   
167  DevilsFoot:445       kgc:subject   
111  DevilsFoot:433         kgc:where   
135  DevilsFoot:438          kgc:whom 

index=367, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
352  DevilsFoot:487            kgc:on   
341  DevilsFoot:484         kgc:where   
355  DevilsFoot:488         kgc:where   
351  DevilsFoot:487   kgc:hasProperty   
214  DevilsFoot:455    kgc:infoSource   
52   DevilsFoot:419    kgc:infoSource   
199  DevilsFoot:451         kgc:where   
344  DevilsFoot:485    kgc:infoSource   
348  DevilsFoot:486    kgc:infoSource   
111  DevilsFoot:433         kgc:where   
170  DevilsFoot:445    kgc:infoSource   
152  DevilsFoot:441    kgc:infoSource   
213  DevilsFoot:455          kgc:whom   
157  DevilsFoot:442    kgc:infoSource   
328  DevilsFoot:481    kgc:infoSource   
361        <mask_e>    kgc:infoSource   
216  DevilsFoot:456    kgc:infoSource   
169  DevilsFoot:445          kgc:whom   
306  DevilsFoot:475    kgc:infoSource   
260  DevilsFoot:467    kgc:infoSource   
302  DevilsFoot:474    kgc:infoSource   
33   DevilsFoot:415         kgc:where   
335  DevilsFoot:482    kgc:infoSource   
318  DevilsFoot:478    kgc:infoSource   
232  DevilsFoot:460    kgc:infoSource   
165  DevilsFoot:444    kgc:infoSource   
45   DevilsFoot:418    kgc:infoSource   
264  DevilsFoot:468    kgc:infoSource   
120  DevilsFoot:435         kgc:where   
25   DevilsFoot:413    kgc:infoSource   
284  DevilsFoot:472    kgc:infoSource   
224  DevilsFoot:458    kgc:infoSource   
263  DevilsFoot:468  kgc:hasPredicate   
354  DevilsFoot:488       kgc:subject   
181  DevilsFoot:446    kgc:infoSource   
315  DevilsFoot:477    kgc:infoSource   
252  DevilsFoot:464    kgc:infoSource   
48   DevilsFoot:418          kgc:time   
140  DevilsFoot:439    kgc:infoSource   
220  DevilsFoot:457    kgc:infoSource   
29   DevilsFoot:414    kgc:infoSource   
126  DevilsFoot:436    kgc:infoSource   
278  DevilsFoot:471    kgc:infoSource   
247  DevilsFoot:463    kgc:infoSource   
212  DevilsFoot:455  kgc:hasPredicate   
271  DevilsFoot:470    kgc:infoSource   
268  DevilsFoot:469    kgc:infoSource   
148  DevilsFoot:440    kgc:infoSource   
210  DevilsFoot:454            kgc:to   
34   DevilsFoot:415    kgc:infoSource   
193  DevilsFoot:449    kgc:infoSource   
311  DevilsFoot:476    kgc:infoSource   
50   DevilsFoot:419       kgc:subject   
340  DevilsFoot:484  kgc:hasPredicate   
189  DevilsFoot:448    kgc:infoSource   
262  DevilsFoot:468       kgc:subject   
192  DevilsFoot:449         kgc:where   
79   DevilsFoot:424    kgc:infoSource   
117  DevilsFoot:434    kgc:infoSource   
357  DevilsFoot:489       kgc:subject   
41   DevilsFoot:417    kgc:infoSource   
337  DevilsFoot:483       kgc:subject   
237  DevilsFoot:461    kgc:infoSource   
32   DevilsFoot:415  kgc:hasPredicate   
329  DevilsFoot:481          kgc:from   
3    DevilsFoot:410    kgc:infoSource   
304  DevilsFoot:475       kgc:subject   
156  DevilsFoot:442          kgc:whom   
280  DevilsFoot:472       kgc:subject   
86   DevilsFoot:426          kgc:whom   
75   DevilsFoot:423    kgc:infoSource   
219  DevilsFoot:457  kgc:hasPredicate   
300  DevilsFoot:474       kgc:subject   
208  DevilsFoot:454       kgc:subject   
362        <mask_e>  kgc:hasPredicate   
323  DevilsFoot:480       kgc:subject   
331  DevilsFoot:482       kgc:subject   
197  DevilsFoot:451       kgc:subject   
256  DevilsFoot:466       kgc:subject   
61   DevilsFoot:421    kgc:infoSource   
97   DevilsFoot:429            kgc:on   
159  DevilsFoot:443       kgc:subject   
227  DevilsFoot:459  kgc:hasPredicate   
241  DevilsFoot:462    kgc:infoSource   
367        <mask_e>         kgc:where   
172  DevilsFoot:446       kgc:subject   
266  DevilsFoot:469       kgc:subject   
338  DevilsFoot:483  kgc:hasPredicate   
320  DevilsFoot:479       kgc:subject   
114  DevilsFoot:434  kgc:hasPredicate   
145  DevilsFoot:440       kgc:subject   
347  DevilsFoot:486  kgc:hasPredicate   
168  DevilsFoot:445  kgc:hasPredicate   
350  DevilsFoot:487       kgc:subject   
133  DevilsFoot:438  kgc:hasPredicate   
5    DevilsFoot:411    kgc:infoSource   
334  DevilsFoot:482            kgc:to 

### AbbeyGrange(僧坊荘園)
Who killed Lord Blackenstall? (criminal & explanation)
被害者: Sir_Eustace_Brackenstall
犯人: 
犯行動機:

In [21]:
def do_AbbeyGrange_pred():
    title = 'AbbeyGrange'
    victim_name = 'Sir_Eustace_Brackenstall'
    killer_name = 'Jack_Croker'
    last_index = 414
    story_len = 80

    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_AbbeyGrange_pred()
pass

2023-02-05 09:46:03 - INFO - 3696358453.py - 13 - The pred ranking about AbbeyGrange:Jack_Croker is 2


predicate  \
ranking                                     
0                     word.predicate:kill   
1                         AllTitle:Holmes   
2                      word.predicate:die   
3                  word.predicate:notHave   
4                  word.predicate:notWant   
5                     word.predicate:come   
6                      AbbeyGrange:police   
7                         AllTitle:Watson   
8           AbbeyGrange:Lady_Brackenstall   
9                   DancingMen:Abe_Slaney   
10                     SilverBlaze:police   
11       SilverBlaze:Wife_of_John_Straker   
12                    word.predicate:meet   
13           DateTime:1883-04-02T04:00:00   
14                    word.predicate:hold   
15                   word.predicate:exist   
16                    word.predicate:send   
17                    word.predicate:have   
18                SilverBlaze:Silas_Brown   
19                      DevilsFoot:window   

                                          whom  \
ranking                                          
0                              AllTitle:Holmes   
1                          CrookedMan:Morrison   
2                            DevilsFoot:George   
3                              AllTitle:Watson   
4                           AbbeyGrange:police   
5                AbbeyGrange:Lady_Brackenstall   
6                      AbbeyGrange:Jack_Croker   
7         AbbeyGrange:Sir_Eustace_Brackenstall   
8                 DateTime:1898-08-13T03:02:00   
9                              DevilsFoot:Owen   
10       AbbeyGrange:Burglary_team_of_Lewisham   
11                   SilverBlaze:two_young_men   
12                            CrookedMan:Henry   
13                          word.predicate:say   
14                            CrookedMan:beast   
15               AbbeyGrange:Thought_of_Holmes   
16                        word.predicate:think   
17                 ResidentPatient:Blessington   
18                 SilverBlaze:Fitzroy_Simpson   
19                         word.predicate:meet   

                                        subject  \
ranking                                           
0                                       <bos_e>   
1                               AllTitle:Holmes   
2                       AbbeyGrange:Jack_Croker   
3                               AllTitle:Watson   
4                       SilverBlaze:Silas_Brown   
5                           AbbeyGrange:Theresa   
6                             DancingMen:Cubitt   
7                          word.predicate:shout   
8                           word.predicate:meet   
9                           CrookedMan:Morrison   
10                          DevilsFoot:Mortimer   
11                    DevilsFoot:Doctor_Richard   
12                        word.predicate:become   
13                           word.predicate:say   
14                      word.predicate:notExist   
15                          word.predicate:have   
16                 DateTime:1883-04-01T15:00:00   
17       AbbeyGrange:Thought_of_Stanley_Hopkins   
18                    ResidentPatient:Young_man   
19                    ACaseOfIdentity:Windibank   

                                            why  \
ranking                                           
0                                       <bos_e>   
1                        word.predicate:believe   
2                               AllTitle:Holmes   
3                         word.predicate:become   
4               ResidentPatient:Percy_Trevelyan   
5                  DateTime:1883-04-01T10:00:00   
6                           word.predicate:dead   
7                       AbbeyGrange:Jack_Croker   
8                       word.predicate:consider   
9                           CrookedMan:Morrison   
10                              AllTitle:Watson   
11                          word.predicate:meet   
12                            DancingMen:Cubitt   
13                          word.predicate:have   
1

index=343, triple=['AbbeyGrange:414', 'kgc:hasPredicate', 'word.predicate:cannotFind'], attention list


head          relation  \
280  AbbeyGrange:399a    kgc:infoSource   
273   AbbeyGrange:398    kgc:infoSource   
218   AbbeyGrange:385    kgc:infoSource   
313   AbbeyGrange:406    kgc:infoSource   
317   AbbeyGrange:407    kgc:infoSource   
132   AbbeyGrange:365   kgc:hasProperty   
285   AbbeyGrange:400    kgc:infoSource   
270   AbbeyGrange:397    kgc:infoSource   
28    AbbeyGrange:341   kgc:hasProperty   
282   AbbeyGrange:400       kgc:subject   
319   AbbeyGrange:408       kgc:subject   
229   AbbeyGrange:388  kgc:hasPredicate   
83    AbbeyGrange:353          kgc:what   
290   AbbeyGrange:401    kgc:infoSource   
293   AbbeyGrange:402   kgc:hasProperty   
315   AbbeyGrange:407       kgc:subject   
310   AbbeyGrange:406       kgc:subject   
340   AbbeyGrange:413    kgc:infoSource   
323   AbbeyGrange:409   kgc:hasProperty   
228   AbbeyGrange:388       kgc:subject   
348          <mask_e>          kgc:whom   
302   AbbeyGrange:404          kgc:whom   
231   AbbeyGrange:388    kgc:infoSource   
79    AbbeyGrange:352    kgc:infoSource   
110   AbbeyGrange:359          kgc:whom   
346          <mask_e>    kgc:infoSource   
11    AbbeyGrange:337   kgc:hasProperty   
236   AbbeyGrange:390       kgc:subject   
91    AbbeyGrange:355   kgc:hasProperty   
84    AbbeyGrange:353    kgc:infoSource   
75    AbbeyGrange:351    kgc:infoSource   
122   AbbeyGrange:362          kgc:from   
170   AbbeyGrange:373          kgc:what   
267   AbbeyGrange:397       kgc:subject   
128   AbbeyGrange:364  kgc:hasPredicate   
237   AbbeyGrange:390  kgc:hasPredicate   
62    AbbeyGrange:348          kgc:what   
106   AbbeyGrange:358    kgc:infoSource   
95    AbbeyGrange:356   kgc:hasProperty   
202   AbbeyGrange:381  kgc:hasPredicate   
238   AbbeyGrange:390    kgc:infoSource   
77    AbbeyGrange:352  kgc:hasPredicate   
284   AbbeyGrange:400          kgc:what   
265   AbbeyGrange:396   kgc:hasProperty   
100   AbbeyGrange:357         kgc:where   
111   AbbeyGrange:359    kgc:infoSource   
30    AbbeyGrange:341         kgc:where   
213   AbbeyGrange:384  kgc:hasPredicate   
167   AbbeyGrange:372    kgc:infoSource   
217   AbbeyGrange:385          kgc:what   
114   AbbeyGrange:360    kgc:infoSource   
163   AbbeyGrange:371    kgc:infoSource   
244   AbbeyGrange:391    kgc:infoSource   
25    AbbeyGrange:340    kgc:infoSource   
59    AbbeyGrange:347            kgc:to   
121   AbbeyGrange:362    kgc:infoSource   
342   AbbeyGrange:414       kgc:subject   
195   AbbeyGrange:379          kgc:what   
31    AbbeyGrange:341    kgc:infoSource   
262   AbbeyGrange:395   kgc:hasProperty   
26    AbbeyGrange:340          kgc:from   
269   AbbeyGrange:397          kgc:what   
126   AbbeyGrange:363            kgc:on   
297   AbbeyGrange:403          kgc:whom   
49    AbbeyGrange:345    kgc:infoSource   
4     AbbeyGrange:335    kgc:infoSource   
81    AbbeyGrange:353       kgc:subject   
125   AbbeyGrange:363    kgc:infoSource   
134   AbbeyGrange:365           kgc:why   
298   AbbeyGrange:403    kgc:infoSource   
324   AbbeyGrange:409    kgc:infoSource   
171   AbbeyGrange:373    kgc:infoSource   
335   AbbeyGrange:412   kgc:hasProperty   
174   AbbeyGrange:374          kgc:what   
320   AbbeyGrange:408          kgc:what   
241   AbbeyGrange:391       kgc:subject   
119   AbbeyGrange:361    kgc:infoSource   
275   AbbeyGrange:399       kgc:subject   
29    AbbeyGrange:341          kgc:what   
67    AbbeyGrange:349    kgc:infoSource   
303   AbbeyGrange:404           kgc:why   
308   AbbeyGrange:405           kgc:why   
66    AbbeyGrange:349          kgc:what   
60    AbbeyGrange:347    kgc:infoSource   
331   AbbeyGrange:411  kgc:hasPredicate   
312   AbbeyGrange:406          kgc:what   
214   AbbeyGrange:384          kgc:what   
173   AbbeyGrange:374       kgc:subject   
211   AbbeyGrange:383          kgc:what   
78    AbbeyGrange:352          kgc:what   
208   AbbeyGrange:382    kgc:infoSource   
220   AbbeyGrange:386       kgc:subject   
192   AbbeyGrange:

index=344, triple=['AbbeyGrange:414', 'kgc:what', 'AbbeyGrange:False_charge_person'], attention list


...

head          relation  \
259   AbbeyGrange:394  kgc:hasPredicate   
268   AbbeyGrange:397  kgc:hasPredicate   
335   AbbeyGrange:412   kgc:hasProperty   
41    AbbeyGrange:344  kgc:hasPredicate   
302   AbbeyGrange:404          kgc:whom   
265   AbbeyGrange:396   kgc:hasProperty   
213   AbbeyGrange:384  kgc:hasPredicate   
293   AbbeyGrange:402   kgc:hasProperty   
306   AbbeyGrange:405  kgc:hasPredicate   
347          <mask_e>  kgc:hasPredicate   
253   AbbeyGrange:393   kgc:hasProperty   
272   AbbeyGrange:398  kgc:hasPredicate   
288   AbbeyGrange:401  kgc:hasPredicate   
247   AbbeyGrange:392       kgc:subject   
331   AbbeyGrange:411  kgc:hasPredicate   
169   AbbeyGrange:373  kgc:hasPredicate   
198   AbbeyGrange:380  kgc:hasPredicate   
323   AbbeyGrange:409   kgc:hasProperty   
171   AbbeyGrange:373    kgc:infoSource   
238   AbbeyGrange:390    kgc:infoSource   
237   AbbeyGrange:390  kgc:hasPredicate   
173   AbbeyGrange:374       kgc:subject   
262   AbbeyGrange:395   kgc:hasProperty   
234   AbbeyGrange:389  kgc:hasPredicate   
342   AbbeyGrange:414       kgc:subject   
177   AbbeyGrange:375  kgc:hasPredicate   
295   AbbeyGrange:403  kgc:hasPredicate   
109   AbbeyGrange:359  kgc:hasPredicate   
33    AbbeyGrange:342  kgc:hasPredicate   
104   AbbeyGrange:358  kgc:hasPredicate   
7     AbbeyGrange:336  kgc:hasPredicate   
65    AbbeyGrange:349  kgc:hasPredicate   
301   AbbeyGrange:404  kgc:hasPredicate   
77    AbbeyGrange:352  kgc:hasPredicate   
132   AbbeyGrange:365   kgc:hasProperty   
87    AbbeyGrange:354  kgc:hasPredicate   
221   AbbeyGrange:386  kgc:hasPredicate   
231   AbbeyGrange:388    kgc:infoSource   
110   AbbeyGrange:359          kgc:whom   
242   AbbeyGrange:391  kgc:hasPredicate   
292   AbbeyGrange:402       kgc:subject   
283   AbbeyGrange:400  kgc:hasPredicate   
303   AbbeyGrange:404           kgc:why   
38    AbbeyGrange:343  kgc:hasPredicate   
346          <mask_e>    kgc:infoSource   
297   AbbeyGrange:403          kgc:whom   
11    AbbeyGrange:337   kgc:hasProperty   
334   AbbeyGrange:412       kgc:subject   
137   AbbeyGrange:366  kgc:hasPredicate   
161   AbbeyGrange:371  kgc:hasPredicate   
17    AbbeyGrange:338  kgc:hasPredicate   
276   AbbeyGrange:399  kgc:hasPredicate   
194   AbbeyGrange:379  kgc:hasPredicate   
165   AbbeyGrange:372  kgc:hasPredicate   
229   AbbeyGrange:388  kgc:hasPredicate   
254   AbbeyGrange:393            kgc:to   
216   AbbeyGrange:385  kgc:hasPredicate   
128   AbbeyGrange:364  kgc:hasPredicate   
113   AbbeyGrange:360  kgc:hasPredicate   
241   AbbeyGrange:391       kgc:subject   
300   AbbeyGrange:404       kgc:subject   
74    AbbeyGrange:351  kgc:hasPredicate   
2     AbbeyGrange:335  kgc:hasPredicate   
91    AbbeyGrange:355   kgc:hasProperty   
126   AbbeyGrange:363            kgc:on   
166   AbbeyGrange:372          kgc:what   
210   AbbeyGrange:383  kgc:hasPredicate   
190   AbbeyGrange:378  kgc:hasPredicate   
258   AbbeyGrange:394       kgc:subject   
202   AbbeyGrange:381  kgc:hasPredicate   
37    AbbeyGrange:343       kgc:subject   
273   AbbeyGrange:398    kgc:infoSource   
261   AbbeyGrange:395       kgc:subject   
53    AbbeyGrange:346       kgc:subject   
159   AbbeyGrange:370            kgc:to   
280  AbbeyGrange:399a    kgc:infoSource   
315   AbbeyGrange:407       kgc:subject   
141   AbbeyGrange:367  kgc:hasPredicate   
338   AbbeyGrange:413  kgc:hasPredicate   
207   AbbeyGrange:382  kgc:hasPredicate   
343   AbbeyGrange:414  kgc:hasPredicate   
348          <mask_e>          kgc:whom   
308   AbbeyGrange:405           kgc:why   
319   AbbeyGrange:408       kgc:subject   
244   AbbeyGrange:391    kgc:infoSource   
267   AbbeyGrange:397       kgc:subject   
94    AbbeyGrange:356       kgc:subject   
311   AbbeyGrange:406  kgc:hasPredicate   
236   AbbeyGrange:390       kgc:subject   
264   AbbeyGrange:396       kgc:subject   
239   AbbeyGrange:390           kgc:why   
252   AbbeyGrange:393       kgc:subject   
218   AbbeyGrange:

index=351, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
161   AbbeyGrange:371  kgc:hasPredicate   
82    AbbeyGrange:353  kgc:hasPredicate   
41    AbbeyGrange:344  kgc:hasPredicate   
288   AbbeyGrange:401  kgc:hasPredicate   
38    AbbeyGrange:343  kgc:hasPredicate   
311   AbbeyGrange:406  kgc:hasPredicate   
272   AbbeyGrange:398  kgc:hasPredicate   
346          <mask_e>    kgc:infoSource   
283   AbbeyGrange:400  kgc:hasPredicate   
77    AbbeyGrange:352  kgc:hasPredicate   
302   AbbeyGrange:404          kgc:whom   
216   AbbeyGrange:385  kgc:hasPredicate   
221   AbbeyGrange:386  kgc:hasPredicate   
65    AbbeyGrange:349  kgc:hasPredicate   
7     AbbeyGrange:336  kgc:hasPredicate   
171   AbbeyGrange:373    kgc:infoSource   
79    AbbeyGrange:352    kgc:infoSource   
297   AbbeyGrange:403          kgc:whom   
113   AbbeyGrange:360  kgc:hasPredicate   
33    AbbeyGrange:342  kgc:hasPredicate   
298   AbbeyGrange:403    kgc:infoSource   
198   AbbeyGrange:380  kgc:hasPredicate   
213   AbbeyGrange:384  kgc:hasPredicate   
118   AbbeyGrange:361  kgc:hasPredicate   
282   AbbeyGrange:400       kgc:subject   
247   AbbeyGrange:392       kgc:subject   
306   AbbeyGrange:405  kgc:hasPredicate   
273   AbbeyGrange:398    kgc:infoSource   
342   AbbeyGrange:414       kgc:subject   
295   AbbeyGrange:403  kgc:hasPredicate   
238   AbbeyGrange:390    kgc:infoSource   
285   AbbeyGrange:400    kgc:infoSource   
22    AbbeyGrange:339  kgc:hasPredicate   
202   AbbeyGrange:381  kgc:hasPredicate   
305   AbbeyGrange:405       kgc:subject   
110   AbbeyGrange:359          kgc:whom   
307   AbbeyGrange:405    kgc:infoSource   
280  AbbeyGrange:399a    kgc:infoSource   
111   AbbeyGrange:359    kgc:infoSource   
53    AbbeyGrange:346       kgc:subject   
310   AbbeyGrange:406       kgc:subject   
300   AbbeyGrange:404       kgc:subject   
84    AbbeyGrange:353    kgc:infoSource   
287   AbbeyGrange:401       kgc:subject   
75    AbbeyGrange:351    kgc:infoSource   
279  AbbeyGrange:399a       kgc:subject   
348          <mask_e>          kgc:whom   
338   AbbeyGrange:413  kgc:hasPredicate   
313   AbbeyGrange:406    kgc:infoSource   
268   AbbeyGrange:397  kgc:hasPredicate   
109   AbbeyGrange:359  kgc:hasPredicate   
106   AbbeyGrange:358    kgc:infoSource   
2     AbbeyGrange:335  kgc:hasPredicate   
87    AbbeyGrange:354  kgc:hasPredicate   
340   AbbeyGrange:413    kgc:infoSource   
190   AbbeyGrange:378  kgc:hasPredicate   
31    AbbeyGrange:341    kgc:infoSource   
218   AbbeyGrange:385    kgc:infoSource   
331   AbbeyGrange:411  kgc:hasPredicate   
317   AbbeyGrange:407    kgc:infoSource   
315   AbbeyGrange:407       kgc:subject   
290   AbbeyGrange:401    kgc:infoSource   
259   AbbeyGrange:394  kgc:hasPredicate   
37    AbbeyGrange:343       kgc:subject   
229   AbbeyGrange:388  kgc:hasPredicate   
35    AbbeyGrange:342    kgc:infoSource   
322   AbbeyGrange:409       kgc:subject   
327   AbbeyGrange:410  kgc:hasPredicate   
324   AbbeyGrange:409    kgc:infoSource   
81    AbbeyGrange:353       kgc:subject   
121   AbbeyGrange:362    kgc:infoSource   
275   AbbeyGrange:399       kgc:subject   
328   AbbeyGrange:410    kgc:infoSource   
319   AbbeyGrange:408       kgc:subject   
343   AbbeyGrange:414  kgc:hasPredicate   
270   AbbeyGrange:397    kgc:infoSource   
220   AbbeyGrange:386       kgc:subject   
52    AbbeyGrange:346       kgc:subject   
337   AbbeyGrange:413       kgc:subject   
43    AbbeyGrange:344    kgc:infoSource   
189   AbbeyGrange:378       kgc:subject   
4     AbbeyGrange:335    kgc:infoSource   
74    AbbeyGrange:351  kgc:hasPredicate   
184   AbbeyGrange:377       kgc:subject   
92    AbbeyGrange:355    kgc:infoSource   
103   AbbeyGrange:358       kgc:subject   
241   AbbeyGrange:391       kgc:subject   
167   AbbeyGrange:372    kgc:infoSource   
192   AbbeyGrange:378    kgc:infoSource   
237   AbbeyGrange:390  kgc:hasPredicate   
330   AbbeyGrange:411       kgc:subject   
187   AbbeyGrange:377    kgc:infoSource   
242   AbbeyGrange:

index=352, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
41    AbbeyGrange:344  kgc:hasPredicate   
82    AbbeyGrange:353  kgc:hasPredicate   
272   AbbeyGrange:398  kgc:hasPredicate   
38    AbbeyGrange:343  kgc:hasPredicate   
288   AbbeyGrange:401  kgc:hasPredicate   
216   AbbeyGrange:385  kgc:hasPredicate   
302   AbbeyGrange:404          kgc:whom   
77    AbbeyGrange:352  kgc:hasPredicate   
346          <mask_e>    kgc:infoSource   
311   AbbeyGrange:406  kgc:hasPredicate   
338   AbbeyGrange:413  kgc:hasPredicate   
297   AbbeyGrange:403          kgc:whom   
342   AbbeyGrange:414       kgc:subject   
171   AbbeyGrange:373    kgc:infoSource   
7     AbbeyGrange:336  kgc:hasPredicate   
161   AbbeyGrange:371  kgc:hasPredicate   
283   AbbeyGrange:400  kgc:hasPredicate   
198   AbbeyGrange:380  kgc:hasPredicate   
295   AbbeyGrange:403  kgc:hasPredicate   
247   AbbeyGrange:392       kgc:subject   
110   AbbeyGrange:359          kgc:whom   
238   AbbeyGrange:390    kgc:infoSource   
22    AbbeyGrange:339  kgc:hasPredicate   
300   AbbeyGrange:404       kgc:subject   
109   AbbeyGrange:359  kgc:hasPredicate   
118   AbbeyGrange:361  kgc:hasPredicate   
268   AbbeyGrange:397  kgc:hasPredicate   
273   AbbeyGrange:398    kgc:infoSource   
306   AbbeyGrange:405  kgc:hasPredicate   
213   AbbeyGrange:384  kgc:hasPredicate   
113   AbbeyGrange:360  kgc:hasPredicate   
53    AbbeyGrange:346       kgc:subject   
310   AbbeyGrange:406       kgc:subject   
348          <mask_e>          kgc:whom   
221   AbbeyGrange:386  kgc:hasPredicate   
111   AbbeyGrange:359    kgc:infoSource   
298   AbbeyGrange:403    kgc:infoSource   
280  AbbeyGrange:399a    kgc:infoSource   
87    AbbeyGrange:354  kgc:hasPredicate   
305   AbbeyGrange:405       kgc:subject   
307   AbbeyGrange:405    kgc:infoSource   
282   AbbeyGrange:400       kgc:subject   
33    AbbeyGrange:342  kgc:hasPredicate   
65    AbbeyGrange:349  kgc:hasPredicate   
47    AbbeyGrange:345  kgc:hasPredicate   
313   AbbeyGrange:406    kgc:infoSource   
173   AbbeyGrange:374       kgc:subject   
292   AbbeyGrange:402       kgc:subject   
74    AbbeyGrange:351  kgc:hasPredicate   
327   AbbeyGrange:410  kgc:hasPredicate   
79    AbbeyGrange:352    kgc:infoSource   
37    AbbeyGrange:343       kgc:subject   
287   AbbeyGrange:401       kgc:subject   
285   AbbeyGrange:400    kgc:infoSource   
315   AbbeyGrange:407       kgc:subject   
347          <mask_e>  kgc:hasPredicate   
190   AbbeyGrange:378  kgc:hasPredicate   
290   AbbeyGrange:401    kgc:infoSource   
210   AbbeyGrange:383  kgc:hasPredicate   
218   AbbeyGrange:385    kgc:infoSource   
106   AbbeyGrange:358    kgc:infoSource   
126   AbbeyGrange:363            kgc:on   
84    AbbeyGrange:353    kgc:infoSource   
184   AbbeyGrange:377       kgc:subject   
343   AbbeyGrange:414  kgc:hasPredicate   
279  AbbeyGrange:399a       kgc:subject   
202   AbbeyGrange:381  kgc:hasPredicate   
75    AbbeyGrange:351    kgc:infoSource   
258   AbbeyGrange:394       kgc:subject   
31    AbbeyGrange:341    kgc:infoSource   
331   AbbeyGrange:411  kgc:hasPredicate   
317   AbbeyGrange:407    kgc:infoSource   
340   AbbeyGrange:413    kgc:infoSource   
241   AbbeyGrange:391       kgc:subject   
261   AbbeyGrange:395       kgc:subject   
167   AbbeyGrange:372    kgc:infoSource   
270   AbbeyGrange:397    kgc:infoSource   
229   AbbeyGrange:388  kgc:hasPredicate   
244   AbbeyGrange:391    kgc:infoSource   
94    AbbeyGrange:356       kgc:subject   
121   AbbeyGrange:362    kgc:infoSource   
231   AbbeyGrange:388    kgc:infoSource   
319   AbbeyGrange:408       kgc:subject   
133   AbbeyGrange:365    kgc:infoSource   
92    AbbeyGrange:355    kgc:infoSource   
259   AbbeyGrange:394  kgc:hasPredicate   
35    AbbeyGrange:342    kgc:infoSource   
242   AbbeyGrange:391  kgc:hasPredicate   
337   AbbeyGrange:413       kgc:subject   
2     AbbeyGrange:335  kgc:hasPredicate   
99    AbbeyGrange:357  kgc:hasPredicate   
96    AbbeyGrange:356    kgc:infoSource   
208   AbbeyGrange:

### 入院患者
Who killed Blessington? (criminal & explanation)
被害者: Blessington
犯人: 3人
犯行動機:

In [22]:
def do_ResidentPatient_pred():
    title = 'ResidentPatient'
    victim_name = 'Blessington'
    killer_name = ''
    last_index = 324
    story_len = 80

    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_ResidentPatient_pred()

2023-02-05 09:46:05 - INFO - 3696358453.py - 13 - The pred ranking about ResidentPatient: is -1


predicate  \
ranking                                         
0                         word.predicate:kill   
1                 ResidentPatient:Elderly_man   
2                        word.predicate:enter   
3                             AllTitle:Holmes   
4                         word.predicate:have   
5                       DancingMen:Abe_Slaney   
6                   SpeckledBand:rope_of_bell   
7                          word.predicate:die   
8                          SpeckledBand:Helen   
9                 ResidentPatient:Blessington   
10                         SilverBlaze:police   
11          DevilsFoot:cottage_of_Pordeux_Bay   
12           SilverBlaze:Wife_of_John_Straker   
13                SpeckledBand:metallic_sound   
14                       word.predicate:exist   
15                     DevilsFoot:living_room   
16       AbbeyGrange:Sir_Eustace_Brackenstall   
17                     ACaseOfIdentity:Hosmer   
18              AbbeyGrange:Thought_of_Holmes   
19                       word.predicate:carry   

                                         whom  \
ranking                                         
0                 ResidentPatient:Blessington   
1                 ResidentPatient:Elderly_man   
2                  ResidentPatient:Helper_boy   
3                             AllTitle:Holmes   
4                       DancingMen:Abe_Slaney   
5                DateTime:1898-08-13T03:02:00   
6              SpeckledBand:Roylott_s_bedroom   
7                     word.predicate:notExist   
8                             AllTitle:Watson   
9                         DevilsFoot:Mortimer   
10                   SilverBlaze:Edith_Baxter   
11                          DevilsFoot:George   
12                        word.predicate:know   
13         ResidentPatient:Brook_Street_house   
14                       word.predicate:exist   
15                       word.predicate:visit   
16                        CrookedMan:Morrison   
17                     DevilsFoot:living_room   
18       ACaseOfIdentity:mother_of_Sutherland   
19                        word.predicate:have   

                                 subject                              why  \
ranking                                                                     
0                                <bos_e>                          <bos_e>   
1            ResidentPatient:Blessington                  AllTitle:Watson   
2                        AllTitle:Holmes          word.predicate:notExist   
3                        AllTitle:Watson                  AllTitle:Holmes   
4             ResidentPatient:Helper_boy            word.predicate:return   
5              ResidentPatient:Young_man           SilverBlaze:Ned_Hunter   
6        ResidentPatient:Percy_Trevelyan   SpeckledBand:Roylott_s_bedroom   
7                word.predicate:notExist             word.predicate:exist   
8            ResidentPatient:Elderly_man             word.predicate:close   
9                    AbbeyGrange:Theresa           ACaseOfIdentity:Hosmer   
10        SpeckledBand:Roylott_s_bedroom      ResidentPatient:Elderly_man   
11                  word.predicate:exist       SpeckledBand:1883-04-01T10   
12                ACaseOfIdentity:Hosmer              word.predicate:dead   
13                   DevilsFoot:Mortimer               word.predicate:die   
14               SilverBlaze:Silas_Brown        ResidentPatient:Young_man   
15                     DancingMen:Cubitt            word.predicate:report   
16                  SpeckledBand:Roylott     DateTime:1883-04-01T10:00:00   
17           DancingMen:1898-08-13T03:00          SilverBlaze:Silas_Brown   
18                  AbbeyGrange:Criminal              word.predicate:have   
19                 word.predicate:return  ResidentPatient:Percy_Trevelyan   

                                   what                           where  
ranking                                                                  
0                               <bo

index=343, triple=['ResidentPatient:324', 'kgc:hasProperty', 'word.predicate:want'], attention list


head          relation  \
268  ResidentPatient:305a  kgc:hasPredicate   
272   ResidentPatient:306  kgc:hasPredicate   
14    ResidentPatient:249  kgc:hasPredicate   
18    ResidentPatient:250  kgc:hasPredicate   
331   ResidentPatient:321   kgc:hasProperty   
175   ResidentPatient:285  kgc:hasPredicate   
45    ResidentPatient:256  kgc:hasPredicate   
7     ResidentPatient:247  kgc:hasPredicate   
329   ResidentPatient:320  kgc:hasPredicate   
31    ResidentPatient:253          kgc:time   
148   ResidentPatient:278   kgc:hasProperty   
347              <mask_e>  kgc:hasPredicate   
5     ResidentPatient:246   kgc:hasProperty   
72    ResidentPatient:263   kgc:hasProperty   
49    ResidentPatient:257  kgc:hasPredicate   
3     ResidentPatient:245   kgc:hasProperty   
292   ResidentPatient:312   kgc:hasProperty   
285   ResidentPatient:310   kgc:hasProperty   
335   ResidentPatient:322   kgc:hasProperty   
1     ResidentPatient:245       kgc:subject   
210  ResidentPatient:293a  kgc:hasPredicate   
27    ResidentPatient:253       kgc:subject   
2     ResidentPatient:245       kgc:subject   
339   ResidentPatient:323   kgc:hasProperty   
295   ResidentPatient:313       kgc:subject   
10    ResidentPatient:248  kgc:hasPredicate   
21    ResidentPatient:251   kgc:hasProperty   
343   ResidentPatient:324   kgc:hasProperty   
291   ResidentPatient:312       kgc:subject   
342   ResidentPatient:324       kgc:subject   
299   ResidentPatient:314  kgc:hasPredicate   
246   ResidentPatient:301  kgc:hasPredicate   
289   ResidentPatient:311       kgc:subject   
62    ResidentPatient:261   kgc:hasProperty   
94    ResidentPatient:268   kgc:hasProperty   
171   ResidentPatient:284   kgc:hasProperty   
296   ResidentPatient:313   kgc:hasProperty   
75    ResidentPatient:264   kgc:hasProperty   
170   ResidentPatient:284       kgc:subject   
338   ResidentPatient:323       kgc:subject   
34    ResidentPatient:254  kgc:hasPredicate   
317   ResidentPatient:318   kgc:hasProperty   
284   ResidentPatient:310       kgc:subject   
179   ResidentPatient:286   kgc:hasProperty   
326  ResidentPatient:319a  kgc:hasPredicate   
332   ResidentPatient:321          kgc:when   
77    ResidentPatient:265       kgc:subject   
154   ResidentPatient:280   kgc:hasProperty   
334   ResidentPatient:322       kgc:subject   
24    ResidentPatient:252  kgc:hasPredicate   
167   ResidentPatient:283   kgc:hasProperty   
298   ResidentPatient:314       kgc:subject   
28    ResidentPatient:253   kgc:hasProperty   
78    ResidentPatient:265   kgc:hasProperty   
38    ResidentPatient:255  kgc:hasPredicate   
151   ResidentPatient:279       kgc:subject   
279   ResidentPatient:309       kgc:subject   
271   ResidentPatient:306       kgc:subject   
9     ResidentPatient:248       kgc:subject   
316   ResidentPatient:318       kgc:subject   
124   ResidentPatient:272       kgc:subject   
264   ResidentPatient:304   kgc:hasProperty   
61    ResidentPatient:261       kgc:subject   
250   ResidentPatient:302       kgc:subject   
267  ResidentPatient:305a       kgc:subject   
194   ResidentPatient:290  kgc:hasPredicate   
254   ResidentPatient:302          kgc:time   
178   ResidentPatient:286       kgc:subject   
17    ResidentPatient:250       kgc:subject   
83    ResidentPatient:266   kgc:hasProperty   
346              <mask_e>    kgc:infoSource   
315   ResidentPatient:318       kgc:subject   
261   ResidentPatient:304       kgc:subject   
286   ResidentPatient:310          kgc:when   
282  ResidentPatient:309a  kgc:hasPredicate   
256   ResidentPatient:303       kgc:subject   
33    ResidentPatient:254       kgc:subject   
301   ResidentPatient:315       kgc:subject   
248   ResidentPatient:301          kgc:time   
257   ResidentPatient:303  kgc:hasPredicate   
166   ResidentPatient:283       kgc:subject   
177   ResidentPatient:286       kgc:subject   
174   ResidentPatient:285       kgc:subject   
276   ResidentPatient:308          kgc:whom   
328   ResidentPatient:320 

index=344, triple=['ResidentPatient:324', 'kgc:what', 'ResidentPatient:324a'], attention list


...

index=351, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
100   ResidentPatient:270  kgc:hasPredicate   
329   ResidentPatient:320  kgc:hasPredicate   
251   ResidentPatient:302  kgc:hasPredicate   
326  ResidentPatient:319a  kgc:hasPredicate   
282  ResidentPatient:309a  kgc:hasPredicate   
168   ResidentPatient:283    kgc:infoSource   
231   ResidentPatient:298  kgc:hasPredicate   
96    ResidentPatient:269  kgc:hasPredicate   
210  ResidentPatient:293a  kgc:hasPredicate   
14    ResidentPatient:249  kgc:hasPredicate   
295   ResidentPatient:313       kgc:subject   
164   ResidentPatient:282    kgc:infoSource   
18    ResidentPatient:250  kgc:hasPredicate   
25    ResidentPatient:252          kgc:whom   
101   ResidentPatient:270          kgc:whom   
24    ResidentPatient:252  kgc:hasPredicate   
175   ResidentPatient:285  kgc:hasPredicate   
268  ResidentPatient:305a  kgc:hasPredicate   
302   ResidentPatient:315  kgc:hasPredicate   
257   ResidentPatient:303  kgc:hasPredicate   
49    ResidentPatient:257  kgc:hasPredicate   
38    ResidentPatient:255  kgc:hasPredicate   
311   ResidentPatient:317       kgc:subject   
154   ResidentPatient:280   kgc:hasProperty   
34    ResidentPatient:254  kgc:hasPredicate   
151   ResidentPatient:279       kgc:subject   
272   ResidentPatient:306  kgc:hasPredicate   
31    ResidentPatient:253          kgc:time   
99    ResidentPatient:270       kgc:subject   
299   ResidentPatient:314  kgc:hasPredicate   
292   ResidentPatient:312   kgc:hasProperty   
321   ResidentPatient:319       kgc:subject   
28    ResidentPatient:253   kgc:hasProperty   
316   ResidentPatient:318       kgc:subject   
222   ResidentPatient:296  kgc:hasPredicate   
246   ResidentPatient:301  kgc:hasPredicate   
206   ResidentPatient:293  kgc:hasPredicate   
347              <mask_e>  kgc:hasPredicate   
150   ResidentPatient:279       kgc:subject   
309   ResidentPatient:317       kgc:subject   
342   ResidentPatient:324       kgc:subject   
217   ResidentPatient:295       kgc:subject   
144   ResidentPatient:277       kgc:subject   
209  ResidentPatient:293a       kgc:subject   
298   ResidentPatient:314       kgc:subject   
291   ResidentPatient:312       kgc:subject   
275   ResidentPatient:308  kgc:hasPredicate   
45    ResidentPatient:256  kgc:hasPredicate   
178   ResidentPatient:286       kgc:subject   
185   ResidentPatient:287  kgc:hasPredicate   
21    ResidentPatient:251   kgc:hasProperty   
263   ResidentPatient:304       kgc:subject   
338   ResidentPatient:323       kgc:subject   
346              <mask_e>    kgc:infoSource   
335   ResidentPatient:322   kgc:hasProperty   
225   ResidentPatient:297       kgc:subject   
187   ResidentPatient:288  kgc:hasPredicate   
54    ResidentPatient:258  kgc:hasPredicate   
140   ResidentPatient:276       kgc:subject   
242   ResidentPatient:300  kgc:hasPredicate   
236   ResidentPatient:299       kgc:subject   
221   ResidentPatient:296       kgc:subject   
173   ResidentPatient:285       kgc:subject   
348              <mask_e>          kgc:whom   
314   ResidentPatient:318       kgc:subject   
226   ResidentPatient:297       kgc:subject   
205   ResidentPatient:293       kgc:subject   
48    ResidentPatient:257       kgc:subject   
319   ResidentPatient:319       kgc:subject   
17    ResidentPatient:250       kgc:subject   
241   ResidentPatient:300       kgc:subject   
128   ResidentPatient:273       kgc:subject   
182   ResidentPatient:287       kgc:subject   
214   ResidentPatient:294       kgc:subject   
339   ResidentPatient:323   kgc:hasProperty   
184   ResidentPatient:287       kgc:subject   
262   ResidentPatient:304       kgc:subject   
3     ResidentPatient:245   kgc:hasProperty   
250   ResidentPatient:302       kgc:subject   
334   ResidentPatient:322       kgc:subject   
320   ResidentPatient:319       kgc:subject   
51    ResidentPatient:257            kgc:to   
5     ResidentPatient:246   kgc:hasProperty   
201   ResidentPatient:292       kgc:subject   
248   ResidentPatient:301 

index=352, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
329   ResidentPatient:320  kgc:hasPredicate   
251   ResidentPatient:302  kgc:hasPredicate   
282  ResidentPatient:309a  kgc:hasPredicate   
100   ResidentPatient:270  kgc:hasPredicate   
326  ResidentPatient:319a  kgc:hasPredicate   
168   ResidentPatient:283    kgc:infoSource   
231   ResidentPatient:298  kgc:hasPredicate   
295   ResidentPatient:313       kgc:subject   
96    ResidentPatient:269  kgc:hasPredicate   
175   ResidentPatient:285  kgc:hasPredicate   
292   ResidentPatient:312   kgc:hasProperty   
154   ResidentPatient:280   kgc:hasProperty   
210  ResidentPatient:293a  kgc:hasPredicate   
24    ResidentPatient:252  kgc:hasPredicate   
335   ResidentPatient:322   kgc:hasProperty   
14    ResidentPatient:249  kgc:hasPredicate   
268  ResidentPatient:305a  kgc:hasPredicate   
185   ResidentPatient:287  kgc:hasPredicate   
347              <mask_e>  kgc:hasPredicate   
339   ResidentPatient:323   kgc:hasProperty   
342   ResidentPatient:324       kgc:subject   
18    ResidentPatient:250  kgc:hasPredicate   
3     ResidentPatient:245   kgc:hasProperty   
25    ResidentPatient:252          kgc:whom   
272   ResidentPatient:306  kgc:hasPredicate   
164   ResidentPatient:282    kgc:infoSource   
302   ResidentPatient:315  kgc:hasPredicate   
275   ResidentPatient:308  kgc:hasPredicate   
257   ResidentPatient:303  kgc:hasPredicate   
346              <mask_e>    kgc:infoSource   
101   ResidentPatient:270          kgc:whom   
28    ResidentPatient:253   kgc:hasProperty   
31    ResidentPatient:253          kgc:time   
54    ResidentPatient:258  kgc:hasPredicate   
246   ResidentPatient:301  kgc:hasPredicate   
34    ResidentPatient:254  kgc:hasPredicate   
321   ResidentPatient:319       kgc:subject   
72    ResidentPatient:263   kgc:hasProperty   
242   ResidentPatient:300  kgc:hasPredicate   
298   ResidentPatient:314       kgc:subject   
99    ResidentPatient:270       kgc:subject   
187   ResidentPatient:288  kgc:hasPredicate   
291   ResidentPatient:312       kgc:subject   
299   ResidentPatient:314  kgc:hasPredicate   
7     ResidentPatient:247  kgc:hasPredicate   
316   ResidentPatient:318       kgc:subject   
167   ResidentPatient:283   kgc:hasProperty   
320   ResidentPatient:319       kgc:subject   
148   ResidentPatient:278   kgc:hasProperty   
49    ResidentPatient:257  kgc:hasPredicate   
338   ResidentPatient:323       kgc:subject   
206   ResidentPatient:293  kgc:hasPredicate   
151   ResidentPatient:279       kgc:subject   
311   ResidentPatient:317       kgc:subject   
21    ResidentPatient:251   kgc:hasProperty   
10    ResidentPatient:248  kgc:hasPredicate   
5     ResidentPatient:246   kgc:hasProperty   
315   ResidentPatient:318       kgc:subject   
178   ResidentPatient:286       kgc:subject   
144   ResidentPatient:277       kgc:subject   
191   ResidentPatient:289  kgc:hasPredicate   
312   ResidentPatient:317  kgc:hasPredicate   
348              <mask_e>          kgc:whom   
306   ResidentPatient:316  kgc:hasPredicate   
150   ResidentPatient:279       kgc:subject   
38    ResidentPatient:255  kgc:hasPredicate   
343   ResidentPatient:324   kgc:hasProperty   
45    ResidentPatient:256  kgc:hasPredicate   
140   ResidentPatient:276       kgc:subject   
277   ResidentPatient:308          kgc:when   
174   ResidentPatient:285       kgc:subject   
217   ResidentPatient:295       kgc:subject   
334   ResidentPatient:322       kgc:subject   
179   ResidentPatient:286   kgc:hasProperty   
314   ResidentPatient:318       kgc:subject   
263   ResidentPatient:304       kgc:subject   
310   ResidentPatient:317       kgc:subject   
86    ResidentPatient:266          kgc:time   
173   ResidentPatient:285       kgc:subject   
248   ResidentPatient:301          kgc:time   
78    ResidentPatient:265   kgc:hasProperty   
222   ResidentPatient:296  kgc:hasPredicate   
331   ResidentPatient:321   kgc:hasProperty   
214   ResidentPatient:294       kgc:subject   
162   ResidentPatient:282 

(                                   predicate                         whom  \
 ranking                                                                     
 0                        word.predicate:kill  ResidentPatient:Blessington   
 1                ResidentPatient:Elderly_man  ResidentPatient:Elderly_man   
 2                       word.predicate:enter   ResidentPatient:Helper_boy   
 3                            AllTitle:Holmes              AllTitle:Holmes   
 4                        word.predicate:have        DancingMen:Abe_Slaney   
 ...                                      ...                          ...   
 7844                         AbbeyGrange:293       word.predicate:notWork   
 7845                         AbbeyGrange:178               DevilsFoot:428   
 7846     ResidentPatient:medical_examination        ACaseOfIdentity:Hosma   
 7847                         SilverBlaze:011             DevilsFoot:house   
 7848                         DancingMen:desk              Danci

### 白銀
Who took out the White Silver Blaze? (criminal & explanation) 
被害者: Silver_Blaze
犯人: 
犯行動機:

In [23]:
victim = 'SilverBlaze:Silver_Blaze'
df_ranking_SilverBlaze, df_attension_SilverBlaze = make_ranking(
    'SilverBlaze:330', 'SilverBlaze:396', BRING, MASK_E, MASK_E, MASK_E, victim, MASK_E)

display(df_ranking_SilverBlaze.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_SilverBlaze)
for i in range(len_-20, len_):
    display(i, df_attension_SilverBlaze.iloc[i,:3].tolist())
    display(df_attension_SilverBlaze.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                              whom  \
0                  word.predicate:go          SilverBlaze:Silver_Blaze   
1                    AllTitle:Holmes           SilverBlaze:Silas_Brown   
2                 word.predicate:ask     SilverBlaze:Inspector_Gregory   
3                word.predicate:have          SilverBlaze:John_Straker   
4                word.predicate:kill               AbbeyGrange:Theresa   
5                 SpeckledBand:Helen                   AllTitle:Watson   
6               SpeckledBand:Roylott       SilverBlaze:Fitzroy_Simpson   
7           SilverBlaze:John_Straker        SpeckledBand:1883-04-02T04   
8             SilverBlaze:Desborough                           <bos_e>   
9              DancingMen:Abe_Slaney                   AllTitle:Holmes   
10        SpeckledBand:1883-04-02T04              word.predicate:close   
11             word.predicate:asleep            SilverBlaze:Ned_Hunter   
12     SilverBlaze:Inspector_Gregory                word.predicate:die   
13            word.predicate:request  SilverBlaze:Wife_of_John_Straker   
14          AbbeyGrange:cord_of_bell            ACaseOfIdentity:Hosmer   
15      DateTime:1898-08-13T03:00:00             word.predicate:return   
16               AbbeyGrange:Theresa       ResidentPatient:Blessington   
17  SilverBlaze:Youth_stables_number            word.predicate:notHave   
18                 DevilsFoot:George                  CrookedMan:Nancy   
19            word.predicate:collect              word.predicate:marry   

                             subject                              why  \
0                            <bos_e>             word.predicate:exist   
1            SilverBlaze:Silas_Brown                  AllTitle:Watson   
2           SilverBlaze:Silver_Blaze                          <bos_e>   
3                    AllTitle:Holmes                  AllTitle:Holmes   
4                    AllTitle:Watson              word.predicate:have   
5             SilverBlaze:Ned_Hunter          SilverBlaze:Silas_Brown   
6                AbbeyGrange:Theresa            word.predicate:return   
7   SilverBlaze:Wife_of_John_Straker                 CrookedMan:Nancy   
8         SpeckledBand:1883-04-02T04           word.predicate:believe   
9               SpeckledBand:Roylott            DancingMen:Abe_Slaney   
10            word.predicate:notHave   SpeckledBand:Roylott_s_bedroom   
11                word.predicate:die           SilverBlaze:Ned_Hunter   
12                 DevilsFoot:George     DateTime:1883-04-01T15:00:00   
13             word.predicate:return  ResidentPatient:Percy_Trevelyan   
14             DancingMen:Abe_Slaney                  DevilsFoot:lamp   
15     SilverBlaze:Inspector_Gregory              word.predicate:meet   
16               word.predicate:have          word.predicate:consider   
17          SilverBlaze:Colonel_Ross         SilverBlaze:Edith_Baxter   
18      DateTime:1883-04-01T15:00:00     DateTime:1883-04-01T10:00:00   
19         DevilsFoot:Doctor_Richard              word.predicate:dead   

                                     what  \
0                SilverBlaze:Silver_Blaze   
1                                 <bos_e>   
2                 SilverBlaze:Silas_Brown   
3                     AbbeyGrange:Theresa   
4           SilverBlaze:Inspector_Gregory   
5                         AllTitle:Watson   
6                         AllTitle:Holmes   
7              SpeckledBand:1883-04-02T04   
8                  SilverBlaze:Ned_Hunter   
9   SilverBlaze:Footprint_of_Silver_Blaze   
10                     SpeckledBand:money   
11              DevilsFoot:Doctor_Richard   
12            ResidentPatient:Elderly_man   
13                 ACaseOfIdentity:Hosmer   
14                word.predicate:consider   
15               SilverBlaze:Colonel_Ross   
16       SilverBlaze:Wife_of_John_Straker   
17                    word.predicate:have   
18                 word.predicate:notHave   
19                  word.predicate:ret

313

['SilverBlaze:394', 'kgc:hasPredicate', 'word.predicate:buy']

head         relation                               tail  \
287   SilverBlaze:389      kgc:subject           SilverBlaze:Silver_Blaze   
82    SilverBlaze:348         kgc:whom           SilverBlaze:Silver_Blaze   
273   SilverBlaze:386        kgc:where      SilverBlaze:Dent_of_wasteland   
275   SilverBlaze:387      kgc:subject           SilverBlaze:Silver_Blaze   
304   SilverBlaze:393      kgc:subject                    AllTitle:Holmes   
74    SilverBlaze:346  kgc:hasProperty        word.predicate:Silver_Blaze   
94    SilverBlaze:351         kgc:when  SilverBlaze:Night_of_the_incident   
87    SilverBlaze:349      kgc:subject                    AllTitle:Holmes   
85   SilverBlaze:348a           kgc:to            SilverBlaze:Horseracing   
76    SilverBlaze:347      kgc:subject                    AllTitle:Holmes   
324   SilverBlaze:396           kgc:to                    AllTitle:Holmes   
250   SilverBlaze:382         kgc:when  SilverBlaze:Night_of_the_incident   
64    SilverBlaze:345      kgc:subject                    AllTitle:Holmes   
285   SilverBlaze:388         kgc:when                    SilverBlaze:387   
210  SilverBlaze:371a         kgc:what           SilverBlaze:Silver_Blaze   
164   SilverBlaze:360      kgc:subject                    AllTitle:Holmes   
84   SilverBlaze:348a      kgc:subject           SilverBlaze:Silver_Blaze   
80    SilverBlaze:348      kgc:subject                    AllTitle:Holmes   
308  SilverBlaze:393a      kgc:subject                    AllTitle:Holmes   
279  SilverBlaze:387a      kgc:subject           SilverBlaze:Silver_Blaze   

     atten_from313  
287       0.034020  
82        0.025499  
273       0.017527  
275       0.014257  
304       0.013465  
74        0.013168  
94        0.013090  
87        0.012994  
85        0.012549  
76        0.012430  
324       0.012257  
250       0.012234  
64        0.010561  
285       0.010549  
210       0.010066  
164       0.009799  
84        0.009642  
80        0.009581  
308       0.009356  
279       0.008899

----------


...

----------


332

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation                        tail  \
313   SilverBlaze:394  kgc:hasPredicate          word.predicate:buy   
309  SilverBlaze:393a  kgc:hasPredicate      word.predicate:confirm   
294  SilverBlaze:390a  kgc:hasPredicate      word.predicate:stabble   
183   SilverBlaze:364           kgc:why             SilverBlaze:365   
103   SilverBlaze:354  kgc:hasPredicate        word.predicate:infer   
319   SilverBlaze:395           kgc:why             SilverBlaze:394   
85   SilverBlaze:348a            kgc:to     SilverBlaze:Horseracing   
168   SilverBlaze:360           kgc:why             SilverBlaze:362   
14    SilverBlaze:332            kgc:to             AllTitle:Holmes   
167   SilverBlaze:360           kgc:why             SilverBlaze:361   
169   SilverBlaze:360           kgc:why             SilverBlaze:363   
292   SilverBlaze:390  kgc:hasPredicate         word.predicate:fall   
277   SilverBlaze:387           kgc:why            SilverBlaze:387a   
24    SilverBlaze:334            kgc:to             AllTitle:Holmes   
150   SilverBlaze:357           kgc:why             SilverBlaze:358   
164   SilverBlaze:360       kgc:subject             AllTitle:Holmes   
324   SilverBlaze:396            kgc:to             AllTitle:Holmes   
53   SilverBlaze:342a           kgc:why  SilverBlaze:white_forehead   
49    SilverBlaze:342           kgc:why            SilverBlaze:342a   
222   SilverBlaze:374            kgc:to       SilverBlaze:Wasteland   

     atten_from332  
313       0.036485  
309       0.028675  
294       0.022124  
183       0.019584  
103       0.018857  
319       0.017641  
85        0.016299  
168       0.015641  
14        0.015227  
167       0.013379  
169       0.013328  
292       0.012854  
277       0.012763  
24        0.012419  
150       0.010872  
164       0.010550  
324       0.010375  
53        0.010351  
49        0.009977  
222       0.009556

----------


### CrookedMan(背中の曲がった男):
Why did Barclay die?
被害者: Barclay
犯人:
犯行動機:

In [24]:
victim = 'CrookedMan:Barclay'
df_ranking_CrookedMan, df_attension_CrookedMan = make_ranking(
    f'CrookedMan:{373-80+1}', 'CrookedMan:373', DIE, MASK_E, victim, MASK_E, MASK_E, MASK_E)

display(df_ranking_CrookedMan.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_CrookedMan)
for i in range(len_-20, len_):
    display(i, df_attension_CrookedMan.iloc[i,:3].tolist())
    display(df_attension_CrookedMan.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                            whom  \
0             word.predicate:die               CrookedMan:Murphy   
1            word.predicate:have                CrookedMan:Henry   
2                        <bos_e>            word.predicate:exist   
3                AllTitle:Holmes                CrookedMan:Nancy   
4            word.predicate:kill                 AllTitle:Watson   
5           word.predicate:exist                 AllTitle:Holmes   
6         word.predicate:notHave  SpeckledBand:Roylott_s_bedroom   
7        SilverBlaze:Silas_Brown              CrookedMan:Barclay   
8              DevilsFoot:George     ResidentPatient:Blessington   
9          SpeckledBand:corridor                CrookedMan:beast   
10           word.predicate:work             word.predicate:have   
11               AllTitle:Watson            word.predicate:marry   
12        word.predicate:request    DateTime:1883-04-02T03:00:00   
13   ResidentPatient:Elderly_man             word.predicate:meet   
14     SpeckledBand:rope_of_bell                  CrookedMan:man   
15            SpeckledBand:Helen               DevilsFoot:Brenda   
16         DancingMen:Abe_Slaney             word.predicate:talk   
17        SilverBlaze:Ned_Hunter    DateTime:1883-04-02T04:00:00   
18            word.predicate:ask              SpeckledBand:Helen   
19  DateTime:1883-04-02T04:00:00             CrookedMan:coachman   

                               subject                           why  \
0                   CrookedMan:Barclay               AllTitle:Holmes   
1                      AllTitle:Watson                       <bos_e>   
2                  word.predicate:have               AllTitle:Watson   
3                      AllTitle:Holmes           word.predicate:dead   
4                    CrookedMan:Murphy           word.predicate:come   
5                 word.predicate:exist            word.predicate:try   
6                    DevilsFoot:George         DancingMen:Abe_Slaney   
7   ACaseOfIdentity:Personal_statement           word.predicate:have   
8         DateTime:1883-04-01T15:00:00          word.predicate:exist   
9                  word.predicate:meet           word.predicate:meet   
10         ResidentPatient:Blessington   ResidentPatient:Blessington   
11         SilverBlaze:Horseshoe_marks     SpeckledBand:rope_of_bell   
12                word.predicate:marry             CrookedMan:Murphy   
13                 AbbeyGrange:Theresa     CrookedMan:owner_of_lodge   
14                  SpeckledBand:Helen  DateTime:1898-08-13T03:00:00   
15        DevilsFoot:House_of_Trigenis    SpeckledBand:1881-04-01T10   
16                     DevilsFoot:lamp       word.predicate:notExist   
17                  word.predicate:ask    SpeckledBand:1883-04-01T10   
18             SilverBlaze:Silas_Brown  DateTime:1883-04-02T04:00:00   
19                    CrookedMan:beast              CrookedMan:Henry   

                              what                         where  
0                          <bos_e>                       <bos_e>  
1                  AllTitle:Holmes               AllTitle:Holmes  
2                  AllTitle:Watson               AllTitle:Watson  
3             word.predicate:exist             DevilsFoot:window  
4                DevilsFoot:window          word.predicate:exist  
5              AbbeyGrange:Theresa              CrookedMan:Henry  
6           ACaseOfIdentity:Hosmer           AbbeyGrange:Theresa  
7             word.predicate:close           word.predicate:meet  
8              word.predicate:meet            word.predicate:ask  
9                DevilsFoot:George             DevilsFoot:George  
10         word.predicate:notExist           word.predicate:have  
11              SpeckledBand:Helen  DateTime:1883-04-02T04:00:00  
12          word.predicate:notHave          word.predicate:close  
13             DevilsFoot:Mortimer         word.predicate:return  
14    DateTime:1883-04-02T04:00:00       word.predicate:notExist  
15       

334

['CrookedMan:371', 'kgc:subject', 'CrookedMan:Barclay']

head          relation                             tail  \
334   CrookedMan:371       kgc:subject               CrookedMan:Barclay   
335   CrookedMan:371  kgc:hasPredicate               word.predicate:sin   
333   CrookedMan:371       kgc:subject                CrookedMan:Davide   
345   CrookedMan:373    kgc:infoSource                  AllTitle:Holmes   
331   CrookedMan:370    kgc:infoSource                  AllTitle:Holmes   
296  CrookedMan:363a       kgc:subject                  AllTitle:Holmes   
336   CrookedMan:371          kgc:what      CrookedMan:same_kind_of_sin   
338   CrookedMan:372       kgc:subject         CrookedMan:sin_of_Davide   
25    CrookedMan:300       kgc:subject  CrookedMan:old_friends_of_Henry   
347         <mask_e>    kgc:infoSource                  AllTitle:Holmes   
301   CrookedMan:364       kgc:subject                  AllTitle:Holmes   
302   CrookedMan:364       kgc:subject                  AllTitle:Watson   
280   CrookedMan:360       kgc:subject               CrookedMan:Barclay   
146   CrookedMan:325    kgc:infoSource                  AllTitle:Holmes   
330   CrookedMan:370  kgc:hasPredicate               word.predicate:sin   
291   CrookedMan:363       kgc:subject                  AllTitle:Holmes   
328   CrookedMan:369    kgc:infoSource                  AllTitle:Holmes   
136   CrookedMan:322          kgc:whom               CrookedMan:Barclay   
350         <mask_e>       kgc:subject               CrookedMan:Barclay   
326   CrookedMan:369       kgc:subject                CrookedMan:Davide   

     atten_from334  
334       0.019277  
335       0.018512  
333       0.013890  
345       0.011668  
331       0.011199  
296       0.010761  
336       0.010671  
338       0.010581  
25        0.010128  
347       0.009861  
301       0.009495  
302       0.009489  
280       0.008856  
146       0.007836  
330       0.007699  
291       0.007665  
328       0.007542  
136       0.007133  
350       0.007080  
326       0.007067

----------


...

----------


353

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation                      tail  \
320   CrookedMan:368  kgc:hasPredicate        word.predicate:say   
231   CrookedMan:346  kgc:hasPredicate        word.predicate:say   
61    CrookedMan:309  kgc:hasPredicate        word.predicate:say   
307   CrookedMan:365  kgc:hasPredicate        word.predicate:say   
237   CrookedMan:348  kgc:hasPredicate        word.predicate:say   
289   CrookedMan:362         kgc:where  CrookedMan:Hudson_street   
203   CrookedMan:337    kgc:infoSource           AllTitle:Holmes   
297  CrookedMan:363a  kgc:hasPredicate        word.predicate:ask   
331   CrookedMan:370    kgc:infoSource           AllTitle:Holmes   
245   CrookedMan:350  kgc:hasPredicate       word.predicate:call   
347         <mask_e>    kgc:infoSource           AllTitle:Holmes   
176   CrookedMan:331    kgc:infoSource           AllTitle:Holmes   
341   CrookedMan:372    kgc:infoSource           AllTitle:Holmes   
345   CrookedMan:373    kgc:infoSource           AllTitle:Holmes   
303   CrookedMan:364  kgc:hasPredicate    word.predicate:catchUp   
272   CrookedMan:357  kgc:hasPredicate     word.predicate:arrest   
179  CrookedMan:331a  kgc:hasPredicate     word.predicate:reveal   
149   CrookedMan:326  kgc:hasPredicate       word.predicate:call   
351         <mask_e>           kgc:why                  <mask_e>   
174   CrookedMan:331  kgc:hasPredicate    word.predicate:notWant   

     atten_from353  
320       0.026912  
231       0.019299  
61        0.017744  
307       0.015765  
237       0.014423  
289       0.011659  
203       0.011421  
297       0.010577  
331       0.010514  
245       0.010269  
347       0.010223  
176       0.009774  
341       0.009448  
345       0.009247  
303       0.008920  
272       0.008803  
179       0.008756  
149       0.008659  
351       0.008596  
174       0.008099

----------


### 花嫁失踪事件（同一事件）
hozmaの失踪の名瀬を探る
被害者: ACaseOfIdentity:Hozma
犯人: 
犯行動機: 

In [25]:
victim = 'ACaseOfIdentity:Hosmer'
df_ranking_ACaseOfIdentity, df_attension_ACaseOfIdentity = make_ranking(
    'ACaseOfIdentity:510', 'ACaseOfIdentity:578', HIDE, victim, MASK_E, MASK_E, MASK_E, MASK_E)

display(df_ranking_ACaseOfIdentity.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_ACaseOfIdentity)
for i in range(len_-20, len_):
    display(i, df_attension_ACaseOfIdentity.iloc[i,:3].tolist())
    display(df_attension_ACaseOfIdentity.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")


predicate                           whom  \
0            word.predicate:notice         ACaseOfIdentity:Hosmer   
1   SpeckledBand:Roylott_s_bedroom                AllTitle:Holmes   
2              word.predicate:have     ACaseOfIdentity:Sutherland   
3         SilverBlaze:Colonel_Ross              DevilsFoot:George   
4      ResidentPatient:Blessington                AllTitle:Watson   
5                  AllTitle:Holmes  SilverBlaze:Inspector_Gregory   
6             word.predicate:carry               CrookedMan:Henry   
7             word.predicate:visit    ResidentPatient:Blessington   
8           SilverBlaze:Desborough           word.predicate:think   
9               word.predicate:ask                DevilsFoot:Owen   
10               DevilsFoot:George              DevilsFoot:Brenda   
11            SpeckledBand:Roylott      ACaseOfIdentity:Windibank   
12             word.predicate:lose           word.predicate:marry   
13         SilverBlaze:Silas_Brown            word.predicate:have   
14            word.predicate:laugh            word.predicate:fire   
15                SpeckledBand:bed             word.predicate:get   
16            word.predicate:shout           word.predicate:exist   
17    DateTime:1898-08-13T03:02:00         word.predicate:notHave   
18           DancingMen:Abe_Slaney            word.predicate:come   
19                 DevilsFoot:Owen               CrookedMan:Nancy   

                         subject                               why  \
0                        <bos_e>                           <bos_e>   
1      ACaseOfIdentity:Windibank                   AllTitle:Holmes   
2                AllTitle:Watson                   AllTitle:Watson   
3                AllTitle:Holmes               word.predicate:have   
4     ACaseOfIdentity:Sutherland       ResidentPatient:Blessington   
5    ResidentPatient:Blessington               word.predicate:come   
6              DevilsFoot:George              word.predicate:exist   
7              DevilsFoot:window             DancingMen:Abe_Slaney   
8         ACaseOfIdentity:Hosmer                  CrookedMan:Nancy   
9             word.predicate:try               word.predicate:dead   
10  DateTime:1883-04-02T04:00:00           word.predicate:notExist   
11             word.predicate:go       DancingMen:1898-08-13T03:00   
12          word.predicate:shout             word.predicate:arrest   
13           word.predicate:meet      DateTime:1883-04-02T04:00:00   
14             DevilsFoot:Brenda      DateTime:1883-04-01T10:00:00   
15          word.predicate:exist                 DevilsFoot:window   
16           word.predicate:come       ResidentPatient:Elderly_man   
17       word.predicate:notExist         ResidentPatient:Young_man   
18            SpeckledBand:Helen  ResidentPatient:Lanner_Inspector   
19  DateTime:1883-04-01T15:00:00             word.predicate:escape   

                            what                         where  
0                        <bos_e>                       <bos_e>  
1                AllTitle:Holmes               AllTitle:Holmes  
2                AllTitle:Watson               AllTitle:Watson  
3    ResidentPatient:Blessington     ACaseOfIdentity:Windibank  
4         ACaseOfIdentity:Hosmer   ResidentPatient:Blessington  
5        word.predicate:notExist        ACaseOfIdentity:Hosmer  
6      ACaseOfIdentity:Windibank             DevilsFoot:window  
7              DevilsFoot:window       word.predicate:notExist  
8              DevilsFoot:George            word.predicate:say  
9             SpeckledBand:Helen           word.predicate:come  
10           DevilsFoot:Mortimer     ResidentPatient:Young_man  
11           AbbeyGrange:Theresa          word.predicate:shout  
12           word.predicate:come         word.predicate:happen  
13     ResidentPatient:Young_man           AbbeyGrange:Theresa  
14          word.predicate:shout  DateTime:1883-04-02T04:00:00  
15         word.predicate:happen            SpeckledBand:Helen  

293

['ACaseOfIdentity:576', 'kgc:subject', 'ACaseOfIdentity:company']

head          relation  \
289  ACaseOfIdentity:575  kgc:hasPredicate   
293  ACaseOfIdentity:576       kgc:subject   
291  ACaseOfIdentity:575    kgc:infoSource   
259  ACaseOfIdentity:569       kgc:subject   
261  ACaseOfIdentity:569    kgc:infoSource   
295  ACaseOfIdentity:576          kgc:what   
254  ACaseOfIdentity:566    kgc:infoSource   
288  ACaseOfIdentity:575       kgc:subject   
264  ACaseOfIdentity:570  kgc:hasPredicate   
176  ACaseOfIdentity:552          kgc:what   
165  ACaseOfIdentity:549       kgc:subject   
257  ACaseOfIdentity:568          kgc:what   
286  ACaseOfIdentity:574    kgc:infoSource   
169  ACaseOfIdentity:550          kgc:what   
306             <mask_e>    kgc:infoSource   
300  ACaseOfIdentity:577    kgc:infoSource   
168  ACaseOfIdentity:550       kgc:subject   
148  ACaseOfIdentity:543          kgc:what   
119  ACaseOfIdentity:535    kgc:infoSource   
260  ACaseOfIdentity:569          kgc:what   

                                         tail  atten_from293  
289                      word.predicate:match       0.023307  
293                   ACaseOfIdentity:company       0.021428  
291                           AllTitle:Holmes       0.020173  
259                           AllTitle:Holmes       0.016097  
261                           AllTitle:Holmes       0.016027  
295                       ACaseOfIdentity:577       0.014222  
254                           AllTitle:Holmes       0.012414  
288           ACaseOfIdentity:feature_of_type       0.012333  
264                     word.predicate:remove       0.011615  
176                       ACaseOfIdentity:sin       0.011470  
165                       ACaseOfIdentity:law       0.011440  
257  ACaseOfIdentity:handwriting_of_Windibank       0.011089  
286                           AllTitle:Holmes       0.010679  
169                      ACaseOfIdentity:door       0.010259  
306                           AllTitle:Holmes       0.009366  
300        ACaseOfIdentity:someone_of_Company       0.009032  
168                           AllTitle:Holmes       0.008953  
148                       ACaseOfIdentity:law       0.008689  
119                           AllTitle:Holmes       0.008231  
260      ACaseOfIdentity:company_of_Windibank       0.008202

----------


...

----------


312

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation  \
264   ACaseOfIdentity:570  kgc:hasPredicate   
303   ACaseOfIdentity:578  kgc:hasPredicate   
175   ACaseOfIdentity:552  kgc:hasPredicate   
230   ACaseOfIdentity:561  kgc:hasPredicate   
307              <mask_e>  kgc:hasPredicate   
143   ACaseOfIdentity:542  kgc:hasPredicate   
193  ACaseOfIdentity:555a  kgc:hasPredicate   
282   ACaseOfIdentity:573    kgc:infoSource   
58    ACaseOfIdentity:519  kgc:hasPredicate   
306              <mask_e>    kgc:infoSource   
227   ACaseOfIdentity:560    kgc:infoSource   
171   ACaseOfIdentity:551  kgc:hasPredicate   
123   ACaseOfIdentity:537    kgc:infoSource   
60    ACaseOfIdentity:519    kgc:infoSource   
269   ACaseOfIdentity:570          kgc:from   
241   ACaseOfIdentity:563    kgc:infoSource   
160   ACaseOfIdentity:547    kgc:infoSource   
149   ACaseOfIdentity:543    kgc:infoSource   
119   ACaseOfIdentity:535    kgc:infoSource   
166   ACaseOfIdentity:549  kgc:hasPredicate   

                                   tail  atten_from312  
264               word.predicate:remove       0.051680  
303           word.predicate:notBelieve       0.036598  
175                 word.predicate:have       0.022627  
230                 word.predicate:have       0.017258  
307                 word.predicate:hide       0.014897  
143              word.predicate:notKnow       0.013915  
193                  word.predicate:try       0.012465  
282                     AllTitle:Holmes       0.012060  
58                 word.predicate:notGo       0.011547  
306                     AllTitle:Holmes       0.011293  
227                     AllTitle:Holmes       0.011197  
171                  word.predicate:say       0.010912  
123                     AllTitle:Holmes       0.010758  
60                      AllTitle:Holmes       0.010638  
269  ACaseOfIdentity:Personal_statement       0.010583  
241                     AllTitle:Holmes       0.009592  
160           ACaseOfIdentity:Windibank       0.009424  
149           ACaseOfIdentity:Windibank       0.009249  
119                     AllTitle:Holmes       0.008798  
166         word.predicate:cannotHandle       0.008632

----------
